# Модель раннего обнаружения неисправностей промышленного оборудования

# Описание проекта


Предиктивное техническое обслуживание с упором на прогнозирование отказов и принятие мер, в зависимости от
состояния оборудования, для предотвращения отказа или ухудшения характеристик.

In [732]:
import warnings

import numpy as np
import pandas as pd
import pyarrow as pa
import pyarrow.parquet as pq
import dask.array as da
import dask.dataframe as dd
import matplotlib.pyplot as plt
import plotly.graph_objects as go
import plotly.tools as tls
from catboost import CatBoostClassifier
from imblearn.over_sampling import SMOTE
from imblearn.pipeline import Pipeline as imbPipeline
from sklearn.decomposition import PCA
from sklearn.linear_model import LogisticRegression
from sklearn.metrics import confusion_matrix, f1_score, make_scorer
from sklearn.model_selection import GridSearchCV, TimeSeriesSplit, cross_val_score
from sklearn.pipeline import Pipeline
from sklearn.preprocessing import StandardScaler
from sklearn.tree import DecisionTreeClassifier
from statsmodels.tsa.seasonal import seasonal_decompose
from pyts.classification import TimeSeriesForest
from xgboost import XGBClassifier

pd.set_option('display.max_columns', 500)

warnings.simplefilter(action='ignore', category=FutureWarning)

In [372]:
from IPython.display import HTML
import random

def hide_toggle(for_next=False):
    this_cell = """$('div.cell.code_cell.rendered.selected')"""
    next_cell = this_cell + '.next()'

    toggle_text = 'Toggle show/hide'  # text shown on toggle link
    target_cell = this_cell  # target cell to control with toggle
    js_hide_current = ''  # bit of JS to permanently hide code in current cell (only when toggling next cell)

    if for_next:
        target_cell = next_cell
        toggle_text += ' next cell'
        js_hide_current = this_cell + '.find("div.input").hide();'

    js_f_name = 'code_toggle_{}'.format(str(random.randint(1,2**64)))

    html = """
        <script>
            function {f_name}() {{
                {cell_selector}.find('div.input').toggle();
            }}

            {js_hide_current}
        </script>

        <a href="javascript:{f_name}()">{toggle_text}</a>
    """.format(
        f_name=js_f_name,
        cell_selector=target_cell,
        js_hide_current=js_hide_current, 
        toggle_text=toggle_text
    )

    return HTML(html)

hide_toggle()

## Загрузка данных и изучение общей информации <a class="anchor" id="chapter1"></a>

**Загрузка данных**<a class="anchor" id="section_1_1"></a>

In [2]:
dd_X_train = dd.read_parquet(r'D:\хакатон\Датасеты\X_train.parquet', engine='pyarrow')
dd_y_train = dd.read_parquet(r'D:\хакатон\Датасеты\y_train.parquet', engine='pyarrow')

In [607]:
dd_X_test = dd.read_parquet(r'D:\хакатон\Датасеты\X_test.parquet', engine='pyarrow')

Также сосздадим урезанный датасет для просмотра общей информации:

**Информация о размерах таблицы**<a class="anchor" id="section_1_2"></a>

In [ ]:
len(dd_X_train)

In [ ]:
len(dd_X_train.columns)

In [ ]:
dd_X_train.columns

Имеем 9 335 034 рядов и 96 признаков. 

In [ ]:
len(dd_y_train)

In [ ]:
dd_y_train.columns

В таблице таргетов столько же записей, следовательно, таблицы можно спокойно объединять

## Предобработка данных<a class="anchor" id="chapter2"></a>

**Формирование выборок по эксгаустерам**<a class="anchor" id="section_2_2"></a>

In [3]:
dd_X_train_4 = dd.from_pandas(pd.DataFrame(), chunksize = 1000)
dd_X_train_5 = dd.from_pandas(pd.DataFrame(), chunksize = 1000)
dd_X_train_6 = dd.from_pandas(pd.DataFrame(), chunksize = 1000)
dd_X_train_7 = dd.from_pandas(pd.DataFrame(), chunksize = 1000)
dd_X_train_8 = dd.from_pandas(pd.DataFrame(), chunksize = 1000)
dd_X_train_9 = dd.from_pandas(pd.DataFrame(), chunksize = 1000)

In [4]:
for col in dd_X_train.columns:
    if 'ЭКСГАУСТЕР 4' in col:
        dd_X_train_4[col] = dd_X_train[col]
    if 'ЭКСГАУСТЕР 5' in col:
        dd_X_train_5[col] = dd_X_train[col]
    if 'ЭКСГАУСТЕР 6' in col:
        dd_X_train_6[col] = dd_X_train[col]
    if 'ЭКСГАУСТЕР 7' in col:
        dd_X_train_7[col] = dd_X_train[col]
    if 'ЭКСГАУСТЕР 8' in col:
        dd_X_train_8[col] = dd_X_train[col] 
    if 'ЭКСГАУСТЕР 9' in col:
        dd_X_train_9[col] = dd_X_train[col]

In [619]:
dd_X_test_4 = dd.from_pandas(pd.DataFrame(), chunksize = 1000)
for col in dd_X_test.columns:
    if 'ЭКСГАУСТЕР 4' in col:
        dd_X_test_4[col] = dd_X_test[col]

In [5]:
dd_y_train_4 = dd.from_pandas(pd.DataFrame(), chunksize = 1000)
dd_y_train_5 = dd.from_pandas(pd.DataFrame(), chunksize = 1000)
dd_y_train_6 = dd.from_pandas(pd.DataFrame(), chunksize = 1000)
dd_y_train_7 = dd.from_pandas(pd.DataFrame(), chunksize = 1000)
dd_y_train_8 = dd.from_pandas(pd.DataFrame(), chunksize = 1000)
dd_y_train_9 = dd.from_pandas(pd.DataFrame(), chunksize = 1000)

In [6]:
for col in dd_y_train.columns:
    if 'Y_ЭКСГАУСТЕР А/М №4' in col:
        dd_y_train_4[col] = dd_y_train[col]
    if 'Y_ЭКСГАУСТЕР А/М №5' in col:
        dd_y_train_5[col] = dd_y_train[col]
    if 'Y_ЭКСГАУСТЕР А/М №6' in col:
        dd_y_train_6[col] = dd_y_train[col]
    if 'Y_ЭКСГАУСТЕР А/М №7' in col:
        dd_y_train_7[col] = dd_y_train[col]
    if 'Y_ЭКСГАУСТЕР А/М №8' in col:
        dd_y_train_8[col] = dd_y_train[col] 
    if 'Y_ЭКСГАУСТЕР А/М №9' in col:
        dd_y_train_9[col] = dd_y_train[col]

# Исследовательский анализ данных<a class="anchor" id="chapter3"></a>

Прежде всего отбросим ненужные для исследования столбцы

### Анализ параметров эксгаустеров<a class="anchor" id="section_3_1"></a>

In [ ]:
def compute_corr_matrx(X_train_n, threshold):
    """
    Рассчитаем корреляционную матрицу поэтапно, убрав лишние вычисления.

    Аргументы:
        X_train_n(dd.DataFrame): Исходный датафрейм.
        threshold(float): Порог отбрасывания коррелирующих столбцов.

    Выводы:
        tuple: Кортеж из элементов:
            - np.ndarray: Корреляционная матрица.
            - pd.DataFrame: Корреляционная матрица табличного формата с соттветствующими колонками и индексами.
            - list: Список колонок для отбрасывания.
    """
    ar_len = len(X_train_n.columns)
    corr_matrix = np.zeros((ar_len, ar_len))
    to_drop = []

    for i in range(ar_len - 1):
        for j in range(i + 1, ar_len):
            corr_matrix[i][j] = abs(X_train_n[X_train_n.columns[i]].corr(X_train_n[X_train_n.columns[j]]).compute())
            if corr_matrix[i][j] > 0.8:
                to_drop.append(X_train_n.columns[j])

    corr_matrix_t = np.transpose(corr_matrix)
    corr_matrix += corr_matrix_t
    corr_df = pd.DataFrame(corr_matrix, index=X_train_n.columns, columns=X_train_n.columns)

    return corr_matrix, corr_df, to_drop

In [ ]:
%%time
(corr_matrix_4, corr_df_4, to_drop_4) = compute_corr_matrx(dd_X_train_4, 0.8)
(corr_matrix_5, corr_df_5, to_drop_5) = compute_corr_matrx(dd_X_train_5, 0.8)
(corr_matrix_6, corr_df_6, to_drop_6) = compute_corr_matrx(dd_X_train_6, 0.8)
(corr_matrix_7, corr_df_7, to_drop_7) = compute_corr_matrx(dd_X_train_7, 0.8)
(corr_matrix_8, corr_df_8, to_drop_8) = compute_corr_matrx(dd_X_train_8, 0.8)
(corr_matrix_9, corr_df_9, to_drop_9) = compute_corr_matrx(dd_X_train_9, 0.8)

In [ ]:
corr_df_4

Свернутый список:

In [ ]:
hide_toggle()
# to_drop_4 = ['ЭКСГАУСТЕР 4. ТОК РОТОРА2',
#  'ЭКСГАУСТЕР 4. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 2',
#  'ЭКСГАУСТЕР 4. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 3',
#  'ЭКСГАУСТЕР 4. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 4',
#  'ЭКСГАУСТЕР 4. ТЕМПЕРАТУРА МАСЛА В МАСЛОБЛОКЕ',
#  'ЭКСГАУСТЕР 4. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 4',
#  'ЭКСГАУСТЕР 4. ТЕМПЕРАТУРА МАСЛА В МАСЛОБЛОКЕ',
#  'ЭКСГАУСТЕР 4. ТЕМПЕРАТУРА МАСЛА В МАСЛОБЛОКЕ',
#  'ЭКСГАУСТЕР 4. ВИБРАЦИЯ НА ОПОРЕ 3. ПРОДОЛЬНАЯ.',
#  'ЭКСГАУСТЕР 4. ВИБРАЦИЯ НА ОПОРЕ 4. ПРОДОЛЬНАЯ.',
#  'ЭКСГАУСТЕР 4. ВИБРАЦИЯ НА ОПОРЕ 4. ПРОДОЛЬНАЯ.']

In [ ]:
dd_X_train_4_no_corr = dd_X_train_4.drop(list(dict.fromkeys(to_drop_4)), axis=1)

In [ ]:
del corr_df_4, to_drop_4

Ток ротора практически полностью дублируется, что логично.
Также температуры между собой сильно связаны.
Вибрации на каждой из опор не связаны между собой, но продольная почти полностью коррелирует со стандартной.
Если вдруг корреляция прекратится -- сообщение об аномалии!

In [ ]:
corr_df_5

In [ ]:
to_drop_5

Свернутый список:

In [ ]:
hide_toggle()
# to_drop_5 = ['ЭКСГАУСТЕР 5. ТОК РОТОРА 2',
#  'ЭКСГАУСТЕР 5. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 2',
#  'ЭКСГАУСТЕР 5. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 4',
#  'ЭКСГАУСТЕР 5. ТЕМПЕРАТУРА МАСЛА В СИСТЕМЕ',
#  'ЭКСГАУСТЕР 5. ТЕМПЕРАТУРА МАСЛА В МАСЛОБЛОКЕ',
#  'ЭКСГАУСТЕР 5. ТЕМПЕРАТУРА МАСЛА В МАСЛОБЛОКЕ',
#  'ЭКСГАУСТЕР 5. ВИБРАЦИЯ НА ОПОРЕ 3. ПРОДОЛЬНАЯ.',
#  'ЭКСГАУСТЕР 5. ВИБРАЦИЯ НА ОПОРЕ 3',
#  'ЭКСГАУСТЕР 5. ВИБРАЦИЯ НА ОПОРЕ 4. ПРОДОЛЬНАЯ.']


In [ ]:
dd_X_train_5_no_corr = dd_X_train_5.drop(list(dict.fromkeys(to_drop_5)), axis=1)

In [ ]:
del corr_df_5, to_drop_5

Следующий эксгастер немного отличается от предыдущего -- температуры в нем коррелируют не так сильно, а вибрация на опоре 3 связана с опорой 2

In [ ]:
corr_df_6

In [ ]:
to_drop_6

Свернутый список:

In [ ]:
hide_toggle()
# ['ЭКСГАУСТЕР 6. ТОК РОТОРА 2',
#  'ЭКСГАУСТЕР 6. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 2',
#  'ЭКСГАУСТЕР 6. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 3',
#  'ЭКСГАУСТЕР 6. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 4',
#  'ЭКСГАУСТЕР 6. ТЕМПЕРАТУРА МАСЛА В МАСЛОБЛОКЕ',
#  'ЭКСГАУСТЕР 6. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 3',
#  'ЭКСГАУСТЕР 6. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 4',
#  'ЭКСГАУСТЕР 6. ТЕМПЕРАТУРА МАСЛА В МАСЛОБЛОКЕ',
#  'ЭКСГАУСТЕР 6. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 4',
#  'ЭКСГАУСТЕР 6. ТЕМПЕРАТУРА МАСЛА В МАСЛОБЛОКЕ',
#  'ЭКСГАУСТЕР 6. ТЕМПЕРАТУРА МАСЛА В МАСЛОБЛОКЕ']

In [ ]:
dd_X_train_6_no_corr = dd_X_train_6.drop(list(dict.fromkeys(to_drop_6)), axis=1)

In [ ]:
del corr_df_6, to_drop_6

В этом блоке температуры сильно взаимосвязаны друг с другом, а вот вибрации никак не коррелируют

In [ ]:
corr_df_7

In [ ]:
to_drop_7

Свернутый список:

In [ ]:
hide_toggle()
# ['ЭКСГАУСТЕР 7. ТОК РОТОРА 2',
#  'ЭКСГАУСТЕР 7. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 2',
#  'ЭКСГАУСТЕР 7. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 4',
#  'ЭКСГАУСТЕР 7. ТЕМПЕРАТУРА МАСЛА В СИСТЕМЕ',
#  'ЭКСГАУСТЕР 7. ВИБРАЦИЯ НА ОПОРЕ 4']

In [ ]:
dd_X_train_7_no_corr = dd_X_train_7.drop(list(dict.fromkeys(to_drop_7)), axis=1)

In [ ]:
del corr_df_7, to_drop_7

В этой установке мало взаимосвязей параметров, передается несколько температур. Продольная вибрация с опоры 3 передается на опору 4


In [ ]:
corr_df_8

In [ ]:
to_drop_8

Свернутый список:

In [ ]:
hide_toggle()
# ['ЭКСГАУСТЕР 8. ТОК РОТОРА 2',
#  'ЭКСГАУСТЕР 8. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 3',
#  'ЭКСГАУСТЕР 8. ТЕМПЕРАТУРА МАСЛА В СИСТЕМЕ',
#  'ЭКСГАУСТЕР 8. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 4',
#  'ЭКСГАУСТЕР 8. ТЕМПЕРАТУРА МАСЛА В СИСТЕМЕ']

In [ ]:
dd_X_train_8_no_corr = dd_X_train_8.drop(list(dict.fromkeys(to_drop_8)), axis=1)

In [ ]:
del corr_df_8, to_drop_8

В установке 8 параметры еще меньше связаны между собой

In [ ]:
corr_df_9

In [ ]:
to_drop_9

Свернутый список:

In [ ]:
hide_toggle()
# ['ЭКСГАУСТЕР 9. ТОК РОТОРА 2',
#  'ЭКСГАУСТЕР 9. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 2',
#  'ЭКСГАУСТЕР 9. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 3',
#  'ЭКСГАУСТЕР 9. ТЕМПЕРАТУРА МАСЛА В МАСЛОБЛОКЕ',
#  'ЭКСГАУСТЕР 9. ВИБРАЦИЯ НА ОПОРЕ 4']

In [ ]:
dd_X_train_9_no_corr = dd_X_train_9.drop(list(dict.fromkeys(to_drop_9)), axis=1)

In [ ]:
del corr_df_9, to_drop_9

Тут тоже связи незначительные, только добавляется вибрация

**Выводы**

Возможно формирование урезанных выборок для облегчения обучения модели

Примечательно, что установки значительно отличаются между собой, только дублирование тока ротора остается неизменным. Следовательно, для каждой из установок аномальным будет резкое отклонение друг от друга параметров, которые в норме коррелируют.\
Также стоит проверить, будут ли в некоторых эксгаустерах поломки наблюдаться чаще, чем в других. Возможно, теплопередача установки или ее виброизоляция влияют на износ деталей\
\
**Предположения:** 
- В эксгаустерах №4 и №5 поломки будут наблюдаться чаще, чем в других. 
- Эксгаустер №8 имеет меньше всего поломок
- Эксгаустеры №7 и №9 имеют так же мало поломок, но по ним можно посмотреть влияние передаци вибрации в сравнении с №8

### Анализ распределения поломок<a class="anchor" id="section_3_2"></a>

Имеем 2 типа поломок: М1(в таргете 1) -- неисправность, препятствующая дальшейшей работе оборудоввания. Для нее необходимо предсказывать конкретное время до поломки. М2(в таргете 2) -- неисправность, не нарушающая работы оборудования. Тут нужно только определить сам факт поломки (задача классификации)

In [ ]:
y_train = dd_y_train.compute()

In [ ]:
n = 0
for col in y_train.columns[:15]:
    group_temp = y_train.groupby(col)[col].count().compute(optimize_graph=True)
    print(n, group_temp)
    n+=1

Из данных видно, что на элементах встречаются поломки либо только типа 2, либо только типа 1, либо всех сразу. Поскольку для предсказания типов М1 и М3 нужны разные модели, отделим параметры для каждой из них, с учетом того, что кейсы с малым количеством М3 можно исключить

In [ ]:
y_1 = []
y_2 = []
for col in y_train.columns:
    group_temp = y_train.groupby(col)[col].count().compute()
    if group_temp.shape[0] >= 2:
        if group_temp.index[1] == 1:
            y_1.append(col)
        elif group_temp.index[1] == 2 and group_temp[2] >= 1000:
            y_2.append(col)

In [ ]:
len(y_1)

In [ ]:
y_1

In [ ]:
len(y_2)

Серьезные поломки происходили токлько у 34 элементов, а вот мелкие в большинстве

### Связь особенностей эксгаустеров и износа деталей<a class="anchor" id="section_3_3"></a>

Выведем количество деталей с разным типом поломок для каждого эксгаустера

In [ ]:
pd.Series([l[:19] for l in pd.Series(y_1)]).value_counts()

In [ ]:
pd.Series([l[:19] for l in pd.Series(y_2)]).value_counts()

Посчитаем частоту поломок

In [ ]:
y_rates = pd.Series(index = y_train.columns) 
for col in y_train.columns:
    group_temp = y_train.groupby(col)[col].count().compute(optimize_graph=True)
    if group_temp.shape[0] == 1:
        y_rates[col] = 0
    elif group_temp.shape[0] == 2:
        y_rates[col] = group_temp.reset_index(drop=True)[1] / 9335034
    elif group_temp.shape[0] == 3:
        y_rates[col] = (group_temp.reset_index(drop=True)[1] + group_temp.reset_index(drop=True)[2] )/ 9335034
y_rates = y_rates.reset_index()

In [ ]:
for i in range(4, 10):
    rates_sum = 0
    ex_r_len = 1
    for j in range(len(y_rates)):
        if f'Y_ЭКСГАУСТЕР А/М №{i}' in y_rates.loc[j, 'index']:
            rates_sum += y_rates.loc[j, 0]
            ex_r_len += 1
    print(f'Средняя частота поломок в эксгаустере №{i}: ', rates_sum / ex_r_len)

Предположения из раздела "Анализ параметров эксгаустеров" не подтвердились. Несмотря на то, что поломки в эксгаустерах 4 и 5 случаются чуть чаще, в 8 они происходят с такой же частотой.

In [ ]:
del y_train

### Выбор самых важных признаков для каждого таргета (SelectKBest)<a class="anchor" id="section_3_4"></a>

In [ ]:
y_train_4 = dd_y_train_4.compute()

Для выбора самых важных признаков необходимо проверить корреляцию между таргетом и каждыми фичерсами

In [ ]:
def compute_corr_target(X_train_n, y_train_n, threshold):
    """
    Рассчитаем корреляцию между таргетом и каждым признаком.

    Аргументы:
        X_train_n(dd.DataFrame): Исходный датафрейм.
        y_train_n(dd.Series): Столбец рассматриваемого таргета.
        threshold(float): Пороговое значение важных признаков.

    Выводы:
        tuple: Кортеж из элементов:
            - pd.Series: Список всех значений корреляции между таргетом и параметрам.
            - list: Список значений корреляции выше порогового значения.
    """
    corr_series_full = pd.Series(name = y_train_n.name, index = X_train_n.columns)
    corr_series_important_list = []
    for col in X_train_n.columns:
        corr_series_full[col] = abs(X_train_n[col].corr(y_train_n).compute())
        if corr_series_full[col] > threshold:
            corr_series_important_list.append(col)

    return corr_series_full, corr_series_important_list

Свернутый список:

In [782]:
hide_toggle()
# {'ЭЛЕКТРОДВИГАТЕЛЬ ДСПУ-140-84-4 ЭКСГ. №4': ['ЭКСГАУСТЕР 4. ТОК РОТОРА 1',
#   'ЭКСГАУСТЕР 4. ТОК РОТОРА2',
#   'ЭКСГАУСТЕР 4. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 3',
#   'ЭКСГАУСТЕР 4. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 4',
#   'ЭКСГАУСТЕР 4. ТЕМПЕРАТУРА МАСЛА В СИСТЕМЕ',
#   'ЭКСГАУСТЕР 4. ТЕМПЕРАТУРА МАСЛА В МАСЛОБЛОКЕ'],
#  'ПОДШИПНИК ОПОРНЫЙ ЭКСГ. №4': ['ЭКСГАУСТЕР 4. ТОК РОТОРА 1',
#   'ЭКСГАУСТЕР 4. ТОК РОТОРА2',
#   'ЭКСГАУСТЕР 4. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 3',
#   'ЭКСГАУСТЕР 4. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 4',
#   'ЭКСГАУСТЕР 4. ТЕМПЕРАТУРА МАСЛА В СИСТЕМЕ',
#   'ЭКСГАУСТЕР 4. ТЕМПЕРАТУРА МАСЛА В МАСЛОБЛОКЕ',
#   'ЭКСГАУСТЕР 4. ВИБРАЦИЯ НА ОПОРЕ 1'],
#  'УЛИТА ЭКСГ. №4': ['ЭКСГАУСТЕР 4. ТОК РОТОРА 1',
#   'ЭКСГАУСТЕР 4. ТОК РОТОРА2',
#   'ЭКСГАУСТЕР 4. ВИБРАЦИЯ НА ОПОРЕ 1',
#   'ЭКСГАУСТЕР 4. ВИБРАЦИЯ НА ОПОРЕ 3',
#   'ЭКСГАУСТЕР 4. ВИБРАЦИЯ НА ОПОРЕ 3. ПРОДОЛЬНАЯ.',
#   'ЭКСГАУСТЕР 4. ВИБРАЦИЯ НА ОПОРЕ 4. ПРОДОЛЬНАЯ.'],
#  'РЕДУКТОР ГАЗ. ЗАДВИЖКИ ЭКСГ. №4': ['ЭКСГАУСТЕР 4. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 1',
#   'ЭКСГАУСТЕР 4. ВИБРАЦИЯ НА ОПОРЕ 1',
#   'ЭКСГАУСТЕР 4. ВИБРАЦИЯ НА ОПОРЕ 2',
#   'ЭКСГАУСТЕР 4. ВИБРАЦИЯ НА ОПОРЕ 3',
#   'ЭКСГАУСТЕР 4. ВИБРАЦИЯ НА ОПОРЕ 3. ПРОДОЛЬНАЯ.',
#   'ЭКСГАУСТЕР 4. ВИБРАЦИЯ НА ОПОРЕ 4. ПРОДОЛЬНАЯ.'],
#  'МАСЛОНАСОС РАБОЧИЙ ЭКСГ. №4': ['ЭКСГАУСТЕР 4. ТОК РОТОРА 1',
#   'ЭКСГАУСТЕР 4. ТОК РОТОРА2'],
#  'ЭЛЕКТРОАППАРАТУРА ЭКСГ. №4': ['ЭКСГАУСТЕР 4. ТОК РОТОРА 1',
#   'ЭКСГАУСТЕР 4. ТОК РОТОРА2'],
#  'ПОДШИПНИК ОПОРНЫЙ №2 ЭКСГ. №4': ['ЭКСГАУСТЕР 4. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 2'],
#  'ЗАДВИЖКА ЭКСГ. №4': ['ЭКСГАУСТЕР 4. ДАВЛЕНИЕ МАСЛА В СИСТЕМЕ',
#   'ЭКСГАУСТЕР 4. ТЕМПЕРАТУРА МАСЛА В СИСТЕМЕ'],
#  'ГСМ ЭКСГ. №4': ['ЭКСГАУСТЕР 4. ТОК РОТОРА 1',
#   'ЭКСГАУСТЕР 4. ТОК РОТОРА2',
#   'ЭКСГАУСТЕР 4. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 3',
#   'ЭКСГАУСТЕР 4. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 4',
#   'ЭКСГАУСТЕР 4. ТЕМПЕРАТУРА МАСЛА В СИСТЕМЕ',
#   'ЭКСГАУСТЕР 4. ТЕМПЕРАТУРА МАСЛА В МАСЛОБЛОКЕ',
#   'ЭКСГАУСТЕР 4. ВИБРАЦИЯ НА ОПОРЕ 1',
#   'ЭКСГАУСТЕР 4. ВИБРАЦИЯ НА ОПОРЕ 3',
#   'ЭКСГАУСТЕР 4. ВИБРАЦИЯ НА ОПОРЕ 3. ПРОДОЛЬНАЯ.',
#   'ЭКСГАУСТЕР 4. ВИБРАЦИЯ НА ОПОРЕ 4. ПРОДОЛЬНАЯ.'],
#  'ВК 310С ВИБРОПРЕОБРАЗОВАТЕЛЬ ЭКСГ.№4 Т.1': [],
#  'ТСМТ-101-010-50М-400 ТЕРМОПР.ПОДШ.Т.1': [],
#  'РОТОР ЭКСГ. №4': ['ЭКСГАУСТЕР 4. ТОК РОТОРА 1',
#   'ЭКСГАУСТЕР 4. ТОК РОТОРА2',
#   'ЭКСГАУСТЕР 4. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 2',
#   'ЭКСГАУСТЕР 4. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 3',
#   'ЭКСГАУСТЕР 4. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 4',
#   'ЭКСГАУСТЕР 4. ТЕМПЕРАТУРА МАСЛА В СИСТЕМЕ',
#   'ЭКСГАУСТЕР 4. ТЕМПЕРАТУРА МАСЛА В МАСЛОБЛОКЕ',
#   'ЭКСГАУСТЕР 4. ВИБРАЦИЯ НА ОПОРЕ 1'],
#  'МАСЛООХЛАДИТЕЛЬ  М-05-1 ЭКСГ. №4': ['ЭКСГАУСТЕР 4. ТОК РОТОРА 1',
#   'ЭКСГАУСТЕР 4. ТОК РОТОРА2',
#   'ЭКСГАУСТЕР 4. ВИБРАЦИЯ НА ОПОРЕ 1',
#   'ЭКСГАУСТЕР 4. ВИБРАЦИЯ НА ОПОРЕ 2'],
#  'ПОДШИПНИК ОПОРНО-УПОРНЫЙ ЭКСГ. №4': ['ЭКСГАУСТЕР 4. ТОК РОТОРА 1',
#   'ЭКСГАУСТЕР 4. ТОК РОТОРА2',
#   'ЭКСГАУСТЕР 4. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 3',
#   'ЭКСГАУСТЕР 4. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 4',
#   'ЭКСГАУСТЕР 4. ТЕМПЕРАТУРА МАСЛА В МАСЛОБЛОКЕ',
#   'ЭКСГАУСТЕР 4. ВИБРАЦИЯ НА ОПОРЕ 1',
#   'ЭКСГАУСТЕР 4. ВИБРАЦИЯ НА ОПОРЕ 3. ПРОДОЛЬНАЯ.'],
#  'ЭКСГАУСТЕР А/М №4': [],
#  'ЗАП. И РЕГ. АРМАТУРА ЭКСГ.№4': ['ЭКСГАУСТЕР 4. ДАВЛЕНИЕ МАСЛА В СИСТЕМЕ',
#   'ЭКСГАУСТЕР 4. ВИБРАЦИЯ НА ОПОРЕ 2',
#   'ЭКСГАУСТЕР 4. ВИБРАЦИЯ НА ОПОРЕ 3',
#   'ЭКСГАУСТЕР 4. ВИБРАЦИЯ НА ОПОРЕ 3. ПРОДОЛЬНАЯ.',
#   'ЭКСГАУСТЕР 4. ВИБРАЦИЯ НА ОПОРЕ 4. ПРОДОЛЬНАЯ.'],
#  'ПОДШИПНИК ОПОРНЫЙ №1 ЭКСГ. №4': ['ЭКСГАУСТЕР 4. ВИБРАЦИЯ НА ОПОРЕ 2',
#   'ЭКСГАУСТЕР 4. ВИБРАЦИЯ НА ОПОРЕ 4. ПРОДОЛЬНАЯ.'],
#  'ЭЛ/ДВИГАТЕЛЬ ГАЗ. ЗАДВИЖКИ ЭКСГ. №4': ['ЭКСГАУСТЕР 4. ВИБРАЦИЯ НА ОПОРЕ 4. ПРОДОЛЬНАЯ.'],
#  'КЛ1 ТР№4 ДО ЭД ЭКСГАУСТЕРА №4': ['ЭКСГАУСТЕР 4. ТОК РОТОРА 1',
#   'ЭКСГАУСТЕР 4. ТОК РОТОРА2',
#   'ЭКСГАУСТЕР 4. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 1',
#   'ЭКСГАУСТЕР 4. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 3',
#   'ЭКСГАУСТЕР 4. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 4',
#   'ЭКСГАУСТЕР 4. ТЕМПЕРАТУРА МАСЛА В СИСТЕМЕ',
#   'ЭКСГАУСТЕР 4. ТЕМПЕРАТУРА МАСЛА В МАСЛОБЛОКЕ',
#   'ЭКСГАУСТЕР 4. ВИБРАЦИЯ НА ОПОРЕ 1',
#   'ЭКСГАУСТЕР 4. ВИБРАЦИЯ НА ОПОРЕ 2',
#   'ЭКСГАУСТЕР 4. ВИБРАЦИЯ НА ОПОРЕ 3. ПРОДОЛЬНАЯ.'],
#  'КЛ2 ТР№4 ДО ЭД ЭКСГАУСТЕРА №4': ['ЭКСГАУСТЕР 4. ТОК РОТОРА 1',
#   'ЭКСГАУСТЕР 4. ТОК РОТОРА2',
#   'ЭКСГАУСТЕР 4. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 1',
#   'ЭКСГАУСТЕР 4. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 3',
#   'ЭКСГАУСТЕР 4. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 4',
#   'ЭКСГАУСТЕР 4. ТЕМПЕРАТУРА МАСЛА В СИСТЕМЕ',
#   'ЭКСГАУСТЕР 4. ТЕМПЕРАТУРА МАСЛА В МАСЛОБЛОКЕ',
#   'ЭКСГАУСТЕР 4. ВИБРАЦИЯ НА ОПОРЕ 1',
#   'ЭКСГАУСТЕР 4. ВИБРАЦИЯ НА ОПОРЕ 2',
#   'ЭКСГАУСТЕР 4. ВИБРАЦИЯ НА ОПОРЕ 3. ПРОДОЛЬНАЯ.'],
#  'ТР-Р ТМ-4000-10/6 ЭКСГ. №4': ['ЭКСГАУСТЕР 4. ТОК РОТОРА 1',
#   'ЭКСГАУСТЕР 4. ТОК РОТОРА2',
#   'ЭКСГАУСТЕР 4. ДАВЛЕНИЕ МАСЛА В СИСТЕМЕ',
#   'ЭКСГАУСТЕР 4. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 3',
#   'ЭКСГАУСТЕР 4. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 4',
#   'ЭКСГАУСТЕР 4. ТЕМПЕРАТУРА МАСЛА В МАСЛОБЛОКЕ',
#   'ЭКСГАУСТЕР 4. ВИБРАЦИЯ НА ОПОРЕ 1',
#   'ЭКСГАУСТЕР 4. ВИБРАЦИЯ НА ОПОРЕ 2'],
#  'ТИРИСТ. ВОЗБУДИТЕЛЬ ВТ-РЭМ-400 ЭКСГ4 ВУ1': [],
#  'МАСЛОПРОВОДЫ ЭКСГ №4': []}

In [ ]:
%%time
y_X_corr_d_4 = {}
y_X_imp_4_list = {}
for col in y_train_4.columns:
    (
        y_X_corr_d_4[col[20:]], 
        y_X_imp_4_list[col[20:]] 
    ) = compute_corr_target(dd_X_train_4, dd_y_train_4[col], 0.15)

Свернутый список:

In [781]:
hide_toggle()
# {'МАСЛООХЛАДИТЕЛЬ  М-05-1 ЭКСГ. №5': ['ЭКСГАУСТЕР 5. ТОК СТАТОРА',
#   'ЭКСГАУСТЕР 5. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 1',
#   'ЭКСГАУСТЕР 5. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 2',
#   'ЭКСГАУСТЕР 5. ТЕМПЕРАТУРА МАСЛА В МАСЛОБЛОКЕ',
#   'ЭКСГАУСТЕР 5. ВИБРАЦИЯ НА ОПОРЕ 1',
#   'ЭКСГАУСТЕР 5. ВИБРАЦИЯ НА ОПОРЕ 2',
#   'ЭКСГАУСТЕР 5. ВИБРАЦИЯ НА ОПОРЕ 3',
#   'ЭКСГАУСТЕР 5. ВИБРАЦИЯ НА ОПОРЕ 4. ПРОДОЛЬНАЯ.'],
#  'ЭЛЕКТРОДВИГАТЕЛЬ ДСПУ-140-84-4 ЭКСГ. №5': ['ЭКСГАУСТЕР 5. ДАВЛЕНИЕ МАСЛА В СИСТЕМЕ',
#   'ЭКСГАУСТЕР 5. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 2',
#   'ЭКСГАУСТЕР 5. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 3',
#   'ЭКСГАУСТЕР 5. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 4',
#   'ЭКСГАУСТЕР 5. ТЕМПЕРАТУРА МАСЛА В СИСТЕМЕ',
#   'ЭКСГАУСТЕР 5. ТЕМПЕРАТУРА МАСЛА В МАСЛОБЛОКЕ',
#   'ЭКСГАУСТЕР 5. ВИБРАЦИЯ НА ОПОРЕ 1',
#   'ЭКСГАУСТЕР 5. ВИБРАЦИЯ НА ОПОРЕ 2'],
#  'КОРПУС ЭКСГ. №5': ['ЭКСГАУСТЕР 5. ВИБРАЦИЯ НА ОПОРЕ 3'],
#  'ЗАДВИЖКА ЭКСГ. №5': ['ЭКСГАУСТЕР 5. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 4',
#   'ЭКСГАУСТЕР 5. ВИБРАЦИЯ НА ОПОРЕ 1',
#   'ЭКСГАУСТЕР 5. ВИБРАЦИЯ НА ОПОРЕ 2',
#   'ЭКСГАУСТЕР 5. ВИБРАЦИЯ НА ОПОРЕ 3',
#   'ЭКСГАУСТЕР 5. ВИБРАЦИЯ НА ОПОРЕ 4'],
#  'ПОДШИПНИК ОПОРНЫЙ ЭКСГ. №5': ['ЭКСГАУСТЕР 5. ТОК РОТОРА 1',
#   'ЭКСГАУСТЕР 5. ТОК РОТОРА 2',
#   'ЭКСГАУСТЕР 5. ТОК СТАТОРА',
#   'ЭКСГАУСТЕР 5. ДАВЛЕНИЕ МАСЛА В СИСТЕМЕ',
#   'ЭКСГАУСТЕР 5. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 2',
#   'ЭКСГАУСТЕР 5. ВИБРАЦИЯ НА ОПОРЕ 3',
#   'ЭКСГАУСТЕР 5. ВИБРАЦИЯ НА ОПОРЕ 4',
#   'ЭКСГАУСТЕР 5. ВИБРАЦИЯ НА ОПОРЕ 4. ПРОДОЛЬНАЯ.'],
#  'ПОДШИПНИК ОПОРНЫЙ №2': ['ЭКСГАУСТЕР 5. ТОК РОТОРА 1',
#   'ЭКСГАУСТЕР 5. ТОК РОТОРА 2',
#   'ЭКСГАУСТЕР 5. ТОК СТАТОРА',
#   'ЭКСГАУСТЕР 5. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 1',
#   'ЭКСГАУСТЕР 5. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 2',
#   'ЭКСГАУСТЕР 5. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 3',
#   'ЭКСГАУСТЕР 5. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 4',
#   'ЭКСГАУСТЕР 5. ТЕМПЕРАТУРА МАСЛА В МАСЛОБЛОКЕ',
#   'ЭКСГАУСТЕР 5. ВИБРАЦИЯ НА ОПОРЕ 3',
#   'ЭКСГАУСТЕР 5. ВИБРАЦИЯ НА ОПОРЕ 4',
#   'ЭКСГАУСТЕР 5. ВИБРАЦИЯ НА ОПОРЕ 4. ПРОДОЛЬНАЯ.'],
#  'ПОДШИПНИК ОПОРНО-УПОРНЫЙ ЭКСГ. №5': ['ЭКСГАУСТЕР 5. ДАВЛЕНИЕ МАСЛА В СИСТЕМЕ',
#   'ЭКСГАУСТЕР 5. ТЕМПЕРАТУРА МАСЛА В МАСЛОБЛОКЕ'],
#  'МАСЛОНАСОС ШЕСТЕРЕНЧАТЫЙ (РЕЗ.) ЭКСГ. №5': ['ЭКСГАУСТЕР 5. ТОК РОТОРА 2',
#   'ЭКСГАУСТЕР 5. ТОК СТАТОРА',
#   'ЭКСГАУСТЕР 5. ДАВЛЕНИЕ МАСЛА В СИСТЕМЕ',
#   'ЭКСГАУСТЕР 5. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 3',
#   'ЭКСГАУСТЕР 5. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 4',
#   'ЭКСГАУСТЕР 5. ТЕМПЕРАТУРА МАСЛА В СИСТЕМЕ',
#   'ЭКСГАУСТЕР 5. ВИБРАЦИЯ НА ОПОРЕ 3',
#   'ЭКСГАУСТЕР 5. ВИБРАЦИЯ НА ОПОРЕ 4',
#   'ЭКСГАУСТЕР 5. ВИБРАЦИЯ НА ОПОРЕ 4. ПРОДОЛЬНАЯ.'],
#  'ВК 310С ВИБРОПРЕОБРАЗОВАТЕЛЬ ЭКСГ.№5 Т.1': ['ЭКСГАУСТЕР 5. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 3',
#   'ЭКСГАУСТЕР 5. ТЕМПЕРАТУРА МАСЛА В СИСТЕМЕ',
#   'ЭКСГАУСТЕР 5. ВИБРАЦИЯ НА ОПОРЕ 3',
#   'ЭКСГАУСТЕР 5. ВИБРАЦИЯ НА ОПОРЕ 4',
#   'ЭКСГАУСТЕР 5. ВИБРАЦИЯ НА ОПОРЕ 4. ПРОДОЛЬНАЯ.'],
#  'ВК 310С ВИБРОПРЕОБРАЗОВАТЕЛЬ ЭКСГ.№5 Т.3': ['ЭКСГАУСТЕР 5. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 3',
#   'ЭКСГАУСТЕР 5. ТЕМПЕРАТУРА МАСЛА В СИСТЕМЕ',
#   'ЭКСГАУСТЕР 5. ВИБРАЦИЯ НА ОПОРЕ 4',
#   'ЭКСГАУСТЕР 5. ВИБРАЦИЯ НА ОПОРЕ 4. ПРОДОЛЬНАЯ.'],
#  'ЭЛЕКТРООБОРУДОВАНИЯ ЭКСГАУСТЕРА №5': ['ЭКСГАУСТЕР 5. ДАВЛЕНИЕ МАСЛА В СИСТЕМЕ',
#   'ЭКСГАУСТЕР 5. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 3',
#   'ЭКСГАУСТЕР 5. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 4',
#   'ЭКСГАУСТЕР 5. ТЕМПЕРАТУРА МАСЛА В СИСТЕМЕ',
#   'ЭКСГАУСТЕР 5. ВИБРАЦИЯ НА ОПОРЕ 1',
#   'ЭКСГАУСТЕР 5. ВИБРАЦИЯ НА ОПОРЕ 2',
#   'ЭКСГАУСТЕР 5. ВИБРАЦИЯ НА ОПОРЕ 3',
#   'ЭКСГАУСТЕР 5. ВИБРАЦИЯ НА ОПОРЕ 3. ПРОДОЛЬНАЯ.',
#   'ЭКСГАУСТЕР 5. ВИБРАЦИЯ НА ОПОРЕ 4',
#   'ЭКСГАУСТЕР 5. ВИБРАЦИЯ НА ОПОРЕ 4. ПРОДОЛЬНАЯ.'],
#  'ВК 310С ВИБРОПРЕОБРАЗОВАТЕЛЬ ЭКСГ.№5 Т.2': ['ЭКСГАУСТЕР 5. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 3',
#   'ЭКСГАУСТЕР 5. ТЕМПЕРАТУРА МАСЛА В СИСТЕМЕ',
#   'ЭКСГАУСТЕР 5. ВИБРАЦИЯ НА ОПОРЕ 4. ПРОДОЛЬНАЯ.'],
#  'ПОДШИПНИК ОПОРНЫЙ №1': ['ЭКСГАУСТЕР 5. ДАВЛЕНИЕ МАСЛА В СИСТЕМЕ',
#   'ЭКСГАУСТЕР 5. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 3',
#   'ЭКСГАУСТЕР 5. ТЕМПЕРАТУРА МАСЛА В СИСТЕМЕ',
#   'ЭКСГАУСТЕР 5. ТЕМПЕРАТУРА МАСЛА В МАСЛОБЛОКЕ',
#   'ЭКСГАУСТЕР 5. ВИБРАЦИЯ НА ОПОРЕ 1',
#   'ЭКСГАУСТЕР 5. ВИБРАЦИЯ НА ОПОРЕ 2',
#   'ЭКСГАУСТЕР 5. ВИБРАЦИЯ НА ОПОРЕ 3',
#   'ЭКСГАУСТЕР 5. ВИБРАЦИЯ НА ОПОРЕ 4. ПРОДОЛЬНАЯ.'],
#  'РЕДУКТОР ГАЗ. ЗАДВИЖКИ ЭКСГ. №5': ['ЭКСГАУСТЕР 5. ТОК РОТОРА 1',
#   'ЭКСГАУСТЕР 5. ТОК РОТОРА 2',
#   'ЭКСГАУСТЕР 5. ТОК СТАТОРА',
#   'ЭКСГАУСТЕР 5. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 1',
#   'ЭКСГАУСТЕР 5. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 2',
#   'ЭКСГАУСТЕР 5. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 3',
#   'ЭКСГАУСТЕР 5. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 4',
#   'ЭКСГАУСТЕР 5. ТЕМПЕРАТУРА МАСЛА В МАСЛОБЛОКЕ',
#   'ЭКСГАУСТЕР 5. ВИБРАЦИЯ НА ОПОРЕ 3',
#   'ЭКСГАУСТЕР 5. ВИБРАЦИЯ НА ОПОРЕ 4',
#   'ЭКСГАУСТЕР 5. ВИБРАЦИЯ НА ОПОРЕ 4. ПРОДОЛЬНАЯ.'],
#  'ТИРИСТ. ВОЗБУДИТЕЛЬ ВТ-РЭМ-400 ЭКСГ5 ВУ1': [],
#  'ЗАПОРНАЯ АРМАТУРА ЭКСГАУСТЕРА №5': ['ЭКСГАУСТЕР 5. ДАВЛЕНИЕ МАСЛА В СИСТЕМЕ',
#   'ЭКСГАУСТЕР 5. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 1',
#   'ЭКСГАУСТЕР 5. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 2',
#   'ЭКСГАУСТЕР 5. ТЕМПЕРАТУРА МАСЛА В МАСЛОБЛОКЕ',
#   'ЭКСГАУСТЕР 5. ВИБРАЦИЯ НА ОПОРЕ 4. ПРОДОЛЬНАЯ.'],
#  'МАСЛОПРОВОДЫ ЭКСГАУСТЕРА №5': ['ЭКСГАУСТЕР 5. ТОК РОТОРА 1',
#   'ЭКСГАУСТЕР 5. ТОК РОТОРА 2',
#   'ЭКСГАУСТЕР 5. ТОК СТАТОРА',
#   'ЭКСГАУСТЕР 5. ДАВЛЕНИЕ МАСЛА В СИСТЕМЕ',
#   'ЭКСГАУСТЕР 5. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 1',
#   'ЭКСГАУСТЕР 5. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 2',
#   'ЭКСГАУСТЕР 5. ТЕМПЕРАТУРА МАСЛА В МАСЛОБЛОКЕ',
#   'ЭКСГАУСТЕР 5. ВИБРАЦИЯ НА ОПОРЕ 3',
#   'ЭКСГАУСТЕР 5. ВИБРАЦИЯ НА ОПОРЕ 4',
#   'ЭКСГАУСТЕР 5. ВИБРАЦИЯ НА ОПОРЕ 4. ПРОДОЛЬНАЯ.'],
#  'ГСМ ЭКСГ. №5': ['ЭКСГАУСТЕР 5. ТОК РОТОРА 1',
#   'ЭКСГАУСТЕР 5. ТОК РОТОРА 2',
#   'ЭКСГАУСТЕР 5. ТОК СТАТОРА',
#   'ЭКСГАУСТЕР 5. ДАВЛЕНИЕ МАСЛА В СИСТЕМЕ',
#   'ЭКСГАУСТЕР 5. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 2',
#   'ЭКСГАУСТЕР 5. ТЕМПЕРАТУРА МАСЛА В МАСЛОБЛОКЕ',
#   'ЭКСГАУСТЕР 5. ВИБРАЦИЯ НА ОПОРЕ 3',
#   'ЭКСГАУСТЕР 5. ВИБРАЦИЯ НА ОПОРЕ 4',
#   'ЭКСГАУСТЕР 5. ВИБРАЦИЯ НА ОПОРЕ 4. ПРОДОЛЬНАЯ.'],
#  'ЭКСГАУСТЕР А/М №5': [],
#  'ТСМТ-101-010-50М-80 ТЕРМОПРЕОБР.МАСЛО': [],
#  'ТР-Р ТМ-4000-10/6 ЭКСГ. №5': ['ЭКСГАУСТЕР 5. ТОК СТАТОРА',
#   'ЭКСГАУСТЕР 5. ДАВЛЕНИЕ МАСЛА В СИСТЕМЕ',
#   'ЭКСГАУСТЕР 5. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 3',
#   'ЭКСГАУСТЕР 5. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 4',
#   'ЭКСГАУСТЕР 5. ТЕМПЕРАТУРА МАСЛА В СИСТЕМЕ',
#   'ЭКСГАУСТЕР 5. ВИБРАЦИЯ НА ОПОРЕ 1',
#   'ЭКСГАУСТЕР 5. ВИБРАЦИЯ НА ОПОРЕ 2',
#   'ЭКСГАУСТЕР 5. ВИБРАЦИЯ НА ОПОРЕ 4. ПРОДОЛЬНАЯ.'],
#  'КЛ1 ТР№5 ДО ЭД ЭКСГАУСТЕРА №5': ['ЭКСГАУСТЕР 5. ТОК СТАТОРА',
#   'ЭКСГАУСТЕР 5. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 2',
#   'ЭКСГАУСТЕР 5. ВИБРАЦИЯ НА ОПОРЕ 2',
#   'ЭКСГАУСТЕР 5. ВИБРАЦИЯ НА ОПОРЕ 3',
#   'ЭКСГАУСТЕР 5. ВИБРАЦИЯ НА ОПОРЕ 4',
#   'ЭКСГАУСТЕР 5. ВИБРАЦИЯ НА ОПОРЕ 4. ПРОДОЛЬНАЯ.'],
#  'КЛ2 ТР№5 ДО ЭД ЭКСГАУСТЕРА №5': ['ЭКСГАУСТЕР 5. ТОК СТАТОРА',
#   'ЭКСГАУСТЕР 5. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 2',
#   'ЭКСГАУСТЕР 5. ВИБРАЦИЯ НА ОПОРЕ 2',
#   'ЭКСГАУСТЕР 5. ВИБРАЦИЯ НА ОПОРЕ 3',
#   'ЭКСГАУСТЕР 5. ВИБРАЦИЯ НА ОПОРЕ 4',
#   'ЭКСГАУСТЕР 5. ВИБРАЦИЯ НА ОПОРЕ 4. ПРОДОЛЬНАЯ.'],
#  'МАСЛОНАСОС РАБОЧИЙ ЭКСГ. №5': ['ЭКСГАУСТЕР 5. ТОК СТАТОРА',
#   'ЭКСГАУСТЕР 5. ДАВЛЕНИЕ МАСЛА В СИСТЕМЕ',
#   'ЭКСГАУСТЕР 5. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 3',
#   'ЭКСГАУСТЕР 5. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 4',
#   'ЭКСГАУСТЕР 5. ВИБРАЦИЯ НА ОПОРЕ 1',
#   'ЭКСГАУСТЕР 5. ВИБРАЦИЯ НА ОПОРЕ 3',
#   'ЭКСГАУСТЕР 5. ВИБРАЦИЯ НА ОПОРЕ 4',
#   'ЭКСГАУСТЕР 5. ВИБРАЦИЯ НА ОПОРЕ 4. ПРОДОЛЬНАЯ.'],
#  'РОТОР ЭКСГ. №5': ['ЭКСГАУСТЕР 5. ТОК СТАТОРА',
#   'ЭКСГАУСТЕР 5. ДАВЛЕНИЕ МАСЛА В СИСТЕМЕ',
#   'ЭКСГАУСТЕР 5. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 3',
#   'ЭКСГАУСТЕР 5. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 4',
#   'ЭКСГАУСТЕР 5. ВИБРАЦИЯ НА ОПОРЕ 1',
#   'ЭКСГАУСТЕР 5. ВИБРАЦИЯ НА ОПОРЕ 2',
#   'ЭКСГАУСТЕР 5. ВИБРАЦИЯ НА ОПОРЕ 4. ПРОДОЛЬНАЯ.'],
#  'МЕТРАН-100 ДАТЧИКИ ДАВЛЕНИЯ ЭКСГ.№5': [],
#  'ДВИГАТЕЛЬ ПУСКОВОГО МАСЛОНАСОСА ЭКСГ. №5': ['ЭКСГАУСТЕР 5. ДАВЛЕНИЕ МАСЛА В СИСТЕМЕ',
#   'ЭКСГАУСТЕР 5. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 2',
#   'ЭКСГАУСТЕР 5. ВИБРАЦИЯ НА ОПОРЕ 2',
#   'ЭКСГАУСТЕР 5. ВИБРАЦИЯ НА ОПОРЕ 4'],
#  'ГАЗОВАЯ ЗАДВИЖКА ЭКСГАУСТЕРА А/М №5': [],
#  'КОЖУХ МУФТЫ ЭКСГ. №5': ['ЭКСГАУСТЕР 5. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 3',
#   'ЭКСГАУСТЕР 5. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 4',
#   'ЭКСГАУСТЕР 5. ТЕМПЕРАТУРА МАСЛА В СИСТЕМЕ',
#   'ЭКСГАУСТЕР 5. ТЕМПЕРАТУРА МАСЛА В МАСЛОБЛОКЕ',
#   'ЭКСГАУСТЕР 5. ВИБРАЦИЯ НА ОПОРЕ 4. ПРОДОЛЬНАЯ.'],
#  'ТИРИСТ. ВОЗБУДИТЕЛЬ ВТ-РЭМ-400 ЭКСГ5 ВУ2': [],
#  'ТСМТ-101-010-50М-400 ТЕРМОПР.ПОДШ.Т.2': [],
#  'ДВИГАТЕЛЬ РЕЗЕРВНОГО МАСЛОНАСОСА ЭКСГ.№5': [],
#  'ТСМТ-101-010-50М-200 ТЕРМОПР.ПОДШ.Т.3': [],
#  'ЭКСГАУСТЕР Н-8000 А/М №5': []}

%%time
y_X_corr_d_5 = {}
y_X_imp_5_list = {}
for col in y_train_5.columns:
    (
        y_X_corr_d_5[col[20:]], 
        y_X_imp_5_list[col[20:]] 
    ) = compute_corr_target(dd_X_train_5, dd_y_train_5[col], 0.15)

Свернутый список:

In [780]:
hide_toggle()
# {'ЭЛЕКТРОДВИГАТЕЛЬ ДСПУ-140-84-4 ЭКСГ. №6': ['ЭКСГАУСТЕР 6. ТОК РОТОРА 1',
#   'ЭКСГАУСТЕР 6. ТОК РОТОРА 2',
#   'ЭКСГАУСТЕР 6. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 3',
#   'ЭКСГАУСТЕР 6. ТЕМПЕРАТУРА МАСЛА В СИСТЕМЕ',
#   'ЭКСГАУСТЕР 6. ВИБРАЦИЯ НА ОПОРЕ 1',
#   'ЭКСГАУСТЕР 6. ВИБРАЦИЯ НА ОПОРЕ 2',
#   'ЭКСГАУСТЕР 6. ВИБРАЦИЯ НА ОПОРЕ 3'],
#  'КОРПУС ЭКСГ. №6': ['ЭКСГАУСТЕР 6. ТОК РОТОРА 1',
#   'ЭКСГАУСТЕР 6. ТОК РОТОРА 2',
#   'ЭКСГАУСТЕР 6. ВИБРАЦИЯ НА ОПОРЕ 3',
#   'ЭКСГАУСТЕР 6. ВИБРАЦИЯ НА ОПОРЕ 4. ПРОДОЛЬНАЯ.'],
#  'ЗАДВИЖКА ЭКСГ. №6': ['ЭКСГАУСТЕР 6. ТОК РОТОРА 1',
#   'ЭКСГАУСТЕР 6. ТОК РОТОРА 2',
#   'ЭКСГАУСТЕР 6. ДАВЛЕНИЕ МАСЛА В СИСТЕМЕ'],
#  'ПОДШИПНИК ОПОРНЫЙ №2': ['ЭКСГАУСТЕР 6. ТОК РОТОРА 1',
#   'ЭКСГАУСТЕР 6. ТОК РОТОРА 2',
#   'ЭКСГАУСТЕР 6. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 1',
#   'ЭКСГАУСТЕР 6. ВИБРАЦИЯ НА ОПОРЕ 1',
#   'ЭКСГАУСТЕР 6. ВИБРАЦИЯ НА ОПОРЕ 2',
#   'ЭКСГАУСТЕР 6. ВИБРАЦИЯ НА ОПОРЕ 3',
#   'ЭКСГАУСТЕР 6. ВИБРАЦИЯ НА ОПОРЕ 4. ПРОДОЛЬНАЯ.'],
#  'РЕДУКТОР ГАЗ. ЗАДВИЖКИ ЭКСГ. №6': ['ЭКСГАУСТЕР 6. ТОК РОТОРА 1',
#   'ЭКСГАУСТЕР 6. ТОК РОТОРА 2',
#   'ЭКСГАУСТЕР 6. ТЕМПЕРАТУРА МАСЛА В СИСТЕМЕ',
#   'ЭКСГАУСТЕР 6. ВИБРАЦИЯ НА ОПОРЕ 1',
#   'ЭКСГАУСТЕР 6. ВИБРАЦИЯ НА ОПОРЕ 2'],
#  'ПОДШИПНИК ОПОРНО-УПОРНЫЙ ЭКСГ. №6': ['ЭКСГАУСТЕР 6. ТОК РОТОРА 1',
#   'ЭКСГАУСТЕР 6. ТОК РОТОРА 2',
#   'ЭКСГАУСТЕР 6. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 1',
#   'ЭКСГАУСТЕР 6. ВИБРАЦИЯ НА ОПОРЕ 1',
#   'ЭКСГАУСТЕР 6. ВИБРАЦИЯ НА ОПОРЕ 2',
#   'ЭКСГАУСТЕР 6. ВИБРАЦИЯ НА ОПОРЕ 3',
#   'ЭКСГАУСТЕР 6. ВИБРАЦИЯ НА ОПОРЕ 4. ПРОДОЛЬНАЯ.'],
#  'САПФИР 22 МДД РАЗРЕЖЕНИЕ В КОЛЛЕКТОРЕ': [],
#  'МАСЛОБАК ЭКСГ. №6': ['ЭКСГАУСТЕР 6. ТОК РОТОРА 1',
#   'ЭКСГАУСТЕР 6. ТОК РОТОРА 2',
#   'ЭКСГАУСТЕР 6. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 2',
#   'ЭКСГАУСТЕР 6. ВИБРАЦИЯ НА ОПОРЕ 1',
#   'ЭКСГАУСТЕР 6. ВИБРАЦИЯ НА ОПОРЕ 2',
#   'ЭКСГАУСТЕР 6. ВИБРАЦИЯ НА ОПОРЕ 3'],
#  'ПОДШИПНИК ОПОРНЫЙ №1': ['ЭКСГАУСТЕР 6. ТОК РОТОРА 1',
#   'ЭКСГАУСТЕР 6. ТОК РОТОРА 2',
#   'ЭКСГАУСТЕР 6. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 1',
#   'ЭКСГАУСТЕР 6. ВИБРАЦИЯ НА ОПОРЕ 1',
#   'ЭКСГАУСТЕР 6. ВИБРАЦИЯ НА ОПОРЕ 2',
#   'ЭКСГАУСТЕР 6. ВИБРАЦИЯ НА ОПОРЕ 4. ПРОДОЛЬНАЯ.'],
#  'КОЖУХ МУФТЫ ЭКСГ. №6': ['ЭКСГАУСТЕР 6. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 1',
#   'ЭКСГАУСТЕР 6. ВИБРАЦИЯ НА ОПОРЕ 1',
#   'ЭКСГАУСТЕР 6. ВИБРАЦИЯ НА ОПОРЕ 2',
#   'ЭКСГАУСТЕР 6. ВИБРАЦИЯ НА ОПОРЕ 3',
#   'ЭКСГАУСТЕР 6. ВИБРАЦИЯ НА ОПОРЕ 4',
#   'ЭКСГАУСТЕР 6. ВИБРАЦИЯ НА ОПОРЕ 4. ПРОДОЛЬНАЯ.'],
#  'РОТОР ЭКСГ. №6': ['ЭКСГАУСТЕР 6. ТОК РОТОРА 1',
#   'ЭКСГАУСТЕР 6. ТОК РОТОРА 2',
#   'ЭКСГАУСТЕР 6. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 1',
#   'ЭКСГАУСТЕР 6. ВИБРАЦИЯ НА ОПОРЕ 1',
#   'ЭКСГАУСТЕР 6. ВИБРАЦИЯ НА ОПОРЕ 2',
#   'ЭКСГАУСТЕР 6. ВИБРАЦИЯ НА ОПОРЕ 3',
#   'ЭКСГАУСТЕР 6. ВИБРАЦИЯ НА ОПОРЕ 4. ПРОДОЛЬНАЯ.'],
#  'ТР-Р ТМ-4000-10/6 ЭКСГ. №6': ['ЭКСГАУСТЕР 6. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 1',
#   'ЭКСГАУСТЕР 6. ВИБРАЦИЯ НА ОПОРЕ 1'],
#  'ЭЛЕКТРООБОРУДОВАНИЯ ЭКСГ №6': ['ЭКСГАУСТЕР 6. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 1',
#   'ЭКСГАУСТЕР 6. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 2',
#   'ЭКСГАУСТЕР 6. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 3',
#   'ЭКСГАУСТЕР 6. ТЕМПЕРАТУРА МАСЛА В СИСТЕМЕ',
#   'ЭКСГАУСТЕР 6. ТЕМПЕРАТУРА МАСЛА В МАСЛОБЛОКЕ',
#   'ЭКСГАУСТЕР 6. ВИБРАЦИЯ НА ОПОРЕ 1',
#   'ЭКСГАУСТЕР 6. ВИБРАЦИЯ НА ОПОРЕ 2'],
#  'МАСЛООХЛАДИТЕЛЬ  М-05-1 ЭКСГ. №6': ['ЭКСГАУСТЕР 6. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 1',
#   'ЭКСГАУСТЕР 6. ТЕМПЕРАТУРА МАСЛА В СИСТЕМЕ',
#   'ЭКСГАУСТЕР 6. ТЕМПЕРАТУРА МАСЛА В МАСЛОБЛОКЕ',
#   'ЭКСГАУСТЕР 6. ВИБРАЦИЯ НА ОПОРЕ 1',
#   'ЭКСГАУСТЕР 6. ВИБРАЦИЯ НА ОПОРЕ 2'],
#  'САПФИР 22 МДД ПЕРЕПАД ДАВЛ. НА ЦИКЛОНЕ': [],
#  'МАСЛОНАСОС РАБОЧИЙ ЭКСГ. №6': ['ЭКСГАУСТЕР 6. ТОК РОТОРА 1',
#   'ЭКСГАУСТЕР 6. ТОК РОТОРА 2',
#   'ЭКСГАУСТЕР 6. ТОК СТАТОРА',
#   'ЭКСГАУСТЕР 6. ТЕМПЕРАТУРА МАСЛА В СИСТЕМЕ',
#   'ЭКСГАУСТЕР 6. ВИБРАЦИЯ НА ОПОРЕ 1',
#   'ЭКСГАУСТЕР 6. ВИБРАЦИЯ НА ОПОРЕ 2',
#   'ЭКСГАУСТЕР 6. ВИБРАЦИЯ НА ОПОРЕ 3'],
#  'ГАЗОВАЯ ЗАДВИЖКА ЭКСГАУСТЕРА А/М №6': [],
#  'ЭКСГАУСТЕР А/М №6': [],
#  'ПОДШИПНИК ОПОРНЫЙ ЭКСГ. №6': ['ЭКСГАУСТЕР 6. ДАВЛЕНИЕ МАСЛА В СИСТЕМЕ',
#   'ЭКСГАУСТЕР 6. ВИБРАЦИЯ НА ОПОРЕ 1',
#   'ЭКСГАУСТЕР 6. ВИБРАЦИЯ НА ОПОРЕ 3',
#   'ЭКСГАУСТЕР 6. ВИБРАЦИЯ НА ОПОРЕ 4. ПРОДОЛЬНАЯ.'],
#  'ТИРИСТОРНЫЙ ВОЗБУДИТЕЛЬ ТВ-400 ЭКСГ6 ВУ1': [],
#  'ДВИГАТЕЛЬ ПУСКОВОГО МАСЛОНАСОСА ЭКСГ. №6': [],
#  'МАСЛОНАСОС ШЕСТЕРЕНЧАТЫЙ (ПУСК.) ЭКСГ.№6': [],
#  'ВК 310С ВИБРОПРЕОБРАЗОВАТЕЛЬ ЭКСГ.№6 Т.3': [],
#  'МАСЛОПРОВОДЫ ЭКСГ №6': [],
#  'КЛ1 ТР№6 ДО ЭД ЭКСГАУСТЕРА №6': [],
#  'КЛ2 ТР№6 ДО ЭД ЭКСГАУСТЕРА №6': [],
#  'ВК 310С ВИБРОПРЕОБРАЗОВАТЕЛЬ ЭКСГ.№6 Т.2': []}

%%time
y_X_corr_d_6 = {}
y_X_imp_6_list = {}
for col in y_train_6.columns:
    (
        y_X_corr_d_6[col[20:]], 
        y_X_imp_6_list[col[20:]] 
    ) = compute_corr_target(dd_X_train_6, dd_y_train_6[col], 0.15)

Свернутый список:

In [777]:
hide_toggle()
# {'ЭЛЕКТРОДВИГАТЕЛЬ ДСПУ-140-84-4 ЭКСГ. №7': ['ЭКСГАУСТЕР 7. ТОК СТАТОРА',
#   'ЭКСГАУСТЕР 7. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 1',
#   'ЭКСГАУСТЕР 7. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 4',
#   'ЭКСГАУСТЕР 7. ВИБРАЦИЯ НА ОПОРЕ 1',
#   'ЭКСГАУСТЕР 7. ВИБРАЦИЯ НА ОПОРЕ 3',
#   'ЭКСГАУСТЕР 7. ВИБРАЦИЯ НА ОПОРЕ 4'],
#  'КОРПУС ЭКСГ. №7': ['ЭКСГАУСТЕР 7. ТОК СТАТОРА',
#   'ЭКСГАУСТЕР 7. ДАВЛЕНИЕ МАСЛА В СИСТЕМЕ',
#   'ЭКСГАУСТЕР 7. ТЕМПЕРАТУРА МАСЛА В СИСТЕМЕ',
#   'ЭКСГАУСТЕР 7. ВИБРАЦИЯ НА ОПОРЕ 1',
#   'ЭКСГАУСТЕР 7. ВИБРАЦИЯ НА ОПОРЕ 3',
#   'ЭКСГАУСТЕР 7. ВИБРАЦИЯ НА ОПОРЕ 3. ПРОДОЛЬНАЯ.',
#   'ЭКСГАУСТЕР 7. ВИБРАЦИЯ НА ОПОРЕ 4',
#   'ЭКСГАУСТЕР 7. ВИБРАЦИЯ НА ОПОРЕ 4. ПРОДОЛЬНАЯ.'],
#  'ПОДШИПНИК ОПОРНЫЙ №1': ['ЭКСГАУСТЕР 7. ДАВЛЕНИЕ МАСЛА В СИСТЕМЕ',
#   'ЭКСГАУСТЕР 7. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 3',
#   'ЭКСГАУСТЕР 7. ТЕМПЕРАТУРА МАСЛА В СИСТЕМЕ',
#   'ЭКСГАУСТЕР 7. ВИБРАЦИЯ НА ОПОРЕ 3',
#   'ЭКСГАУСТЕР 7. ВИБРАЦИЯ НА ОПОРЕ 4',
#   'ЭКСГАУСТЕР 7. ВИБРАЦИЯ НА ОПОРЕ 4. ПРОДОЛЬНАЯ.'],
#  'ЗАДВИЖКА ЭКСГ. №7': ['ЭКСГАУСТЕР 7. ДАВЛЕНИЕ МАСЛА В СИСТЕМЕ',
#   'ЭКСГАУСТЕР 7. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 1',
#   'ЭКСГАУСТЕР 7. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 2',
#   'ЭКСГАУСТЕР 7. ВИБРАЦИЯ НА ОПОРЕ 1'],
#  'ПОДШИПНИК ОПОРНЫЙ №2': ['ЭКСГАУСТЕР 7. ТОК СТАТОРА',
#   'ЭКСГАУСТЕР 7. ТЕМПЕРАТУРА МАСЛА В СИСТЕМЕ',
#   'ЭКСГАУСТЕР 7. ВИБРАЦИЯ НА ОПОРЕ 1',
#   'ЭКСГАУСТЕР 7. ВИБРАЦИЯ НА ОПОРЕ 2',
#   'ЭКСГАУСТЕР 7. ВИБРАЦИЯ НА ОПОРЕ 3. ПРОДОЛЬНАЯ.',
#   'ЭКСГАУСТЕР 7. ВИБРАЦИЯ НА ОПОРЕ 4',
#   'ЭКСГАУСТЕР 7. ВИБРАЦИЯ НА ОПОРЕ 4. ПРОДОЛЬНАЯ.'],
#  'РОТОР ЭКСГ. №7': ['ЭКСГАУСТЕР 7. ТОК СТАТОРА',
#   'ЭКСГАУСТЕР 7. ДАВЛЕНИЕ МАСЛА В СИСТЕМЕ',
#   'ЭКСГАУСТЕР 7. ВИБРАЦИЯ НА ОПОРЕ 1',
#   'ЭКСГАУСТЕР 7. ВИБРАЦИЯ НА ОПОРЕ 2',
#   'ЭКСГАУСТЕР 7. ВИБРАЦИЯ НА ОПОРЕ 3',
#   'ЭКСГАУСТЕР 7. ВИБРАЦИЯ НА ОПОРЕ 3. ПРОДОЛЬНАЯ.',
#   'ЭКСГАУСТЕР 7. ВИБРАЦИЯ НА ОПОРЕ 4',
#   'ЭКСГАУСТЕР 7. ВИБРАЦИЯ НА ОПОРЕ 4. ПРОДОЛЬНАЯ.'],
#  'ПОДШИПНИК ОПОРНО-УПОРНЫЙ ЭКСГ. №7': ['ЭКСГАУСТЕР 7. ТОК СТАТОРА',
#   'ЭКСГАУСТЕР 7. ДАВЛЕНИЕ МАСЛА В СИСТЕМЕ',
#   'ЭКСГАУСТЕР 7. ВИБРАЦИЯ НА ОПОРЕ 1',
#   'ЭКСГАУСТЕР 7. ВИБРАЦИЯ НА ОПОРЕ 2',
#   'ЭКСГАУСТЕР 7. ВИБРАЦИЯ НА ОПОРЕ 3. ПРОДОЛЬНАЯ.',
#   'ЭКСГАУСТЕР 7. ВИБРАЦИЯ НА ОПОРЕ 4',
#   'ЭКСГАУСТЕР 7. ВИБРАЦИЯ НА ОПОРЕ 4. ПРОДОЛЬНАЯ.'],
#  'ВК 310С ВИБРОПРЕОБРАЗОВАТЕЛЬ ЭКСГ.№7 Т.3': [],
#  'РЕДУКТОР ГАЗ. ЗАДВИЖКИ ЭКСГ. №7': ['ЭКСГАУСТЕР 7. ТОК СТАТОРА',
#   'ЭКСГАУСТЕР 7. ДАВЛЕНИЕ МАСЛА В СИСТЕМЕ',
#   'ЭКСГАУСТЕР 7. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 1',
#   'ЭКСГАУСТЕР 7. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 2',
#   'ЭКСГАУСТЕР 7. ВИБРАЦИЯ НА ОПОРЕ 3',
#   'ЭКСГАУСТЕР 7. ВИБРАЦИЯ НА ОПОРЕ 3. ПРОДОЛЬНАЯ.',
#   'ЭКСГАУСТЕР 7. ВИБРАЦИЯ НА ОПОРЕ 4',
#   'ЭКСГАУСТЕР 7. ВИБРАЦИЯ НА ОПОРЕ 4. ПРОДОЛЬНАЯ.'],
#  'ТСМТ-101-010-50М-80 ТЕРМОПРЕОБР.МАСЛО': [],
#  'ПОДШИПНИК ОПОРНЫЙ ЭКСГ. №7': ['ЭКСГАУСТЕР 7. ТОК СТАТОРА',
#   'ЭКСГАУСТЕР 7. ТЕМПЕРАТУРА МАСЛА В СИСТЕМЕ',
#   'ЭКСГАУСТЕР 7. ВИБРАЦИЯ НА ОПОРЕ 1',
#   'ЭКСГАУСТЕР 7. ВИБРАЦИЯ НА ОПОРЕ 2',
#   'ЭКСГАУСТЕР 7. ВИБРАЦИЯ НА ОПОРЕ 3',
#   'ЭКСГАУСТЕР 7. ВИБРАЦИЯ НА ОПОРЕ 3. ПРОДОЛЬНАЯ.',
#   'ЭКСГАУСТЕР 7. ВИБРАЦИЯ НА ОПОРЕ 4',
#   'ЭКСГАУСТЕР 7. ВИБРАЦИЯ НА ОПОРЕ 4. ПРОДОЛЬНАЯ.'],
#  'ГСМ ЭКСГ. №7': ['ЭКСГАУСТЕР 7. ВИБРАЦИЯ НА ОПОРЕ 1',
#   'ЭКСГАУСТЕР 7. ВИБРАЦИЯ НА ОПОРЕ 4. ПРОДОЛЬНАЯ.'],
#  'КОЖУХ МУФТЫ ЭКСГ. №7': ['ЭКСГАУСТЕР 7. ТОК СТАТОРА',
#   'ЭКСГАУСТЕР 7. ДАВЛЕНИЕ МАСЛА В СИСТЕМЕ',
#   'ЭКСГАУСТЕР 7. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 2',
#   'ЭКСГАУСТЕР 7. ВИБРАЦИЯ НА ОПОРЕ 1',
#   'ЭКСГАУСТЕР 7. ВИБРАЦИЯ НА ОПОРЕ 4',
#   'ЭКСГАУСТЕР 7. ВИБРАЦИЯ НА ОПОРЕ 4. ПРОДОЛЬНАЯ.'],
#  'ЭКСГАУСТЕР А/М №7': [],
#  'МАСЛОПРОВОДЫ ЭКСГАУСТЕРА №7': ['ЭКСГАУСТЕР 7. ДАВЛЕНИЕ МАСЛА В СИСТЕМЕ',
#   'ЭКСГАУСТЕР 7. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 2',
#   'ЭКСГАУСТЕР 7. ВИБРАЦИЯ НА ОПОРЕ 3',
#   'ЭКСГАУСТЕР 7. ВИБРАЦИЯ НА ОПОРЕ 4',
#   'ЭКСГАУСТЕР 7. ВИБРАЦИЯ НА ОПОРЕ 4. ПРОДОЛЬНАЯ.'],
#  'МАСЛООХЛАДИТЕЛЬ  М-05-1 ЭКСГ. №7': ['ЭКСГАУСТЕР 7. ВИБРАЦИЯ НА ОПОРЕ 1'],
#  'САПФИР 22 МДД ПЕРЕПАД ДАВЛ. НА ЦИКЛОНЕ': [],
#  'ЭЛЕКТРООБОРУДОВАНИЯ ЭКСГАУСТЕРА №7': [],
#  'МАСЛОНАСОС РАБОЧИЙ ЭКСГ. №7': ['ЭКСГАУСТЕР 7. ТОК СТАТОРА',
#   'ЭКСГАУСТЕР 7. ДАВЛЕНИЕ МАСЛА В СИСТЕМЕ',
#   'ЭКСГАУСТЕР 7. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 1',
#   'ЭКСГАУСТЕР 7. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 2',
#   'ЭКСГАУСТЕР 7. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 3',
#   'ЭКСГАУСТЕР 7. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 4',
#   'ЭКСГАУСТЕР 7. ТЕМПЕРАТУРА МАСЛА В СИСТЕМЕ',
#   'ЭКСГАУСТЕР 7. ВИБРАЦИЯ НА ОПОРЕ 1',
#   'ЭКСГАУСТЕР 7. ВИБРАЦИЯ НА ОПОРЕ 2',
#   'ЭКСГАУСТЕР 7. ВИБРАЦИЯ НА ОПОРЕ 4',
#   'ЭКСГАУСТЕР 7. ВИБРАЦИЯ НА ОПОРЕ 4. ПРОДОЛЬНАЯ.'],
#  'МАСЛОНАСОС ШЕСТЕРЕНЧАТЫЙ (ПУСК.) ЭКСГ.№7': ['ЭКСГАУСТЕР 7. ТОК СТАТОРА',
#   'ЭКСГАУСТЕР 7. ДАВЛЕНИЕ МАСЛА В СИСТЕМЕ',
#   'ЭКСГАУСТЕР 7. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 1',
#   'ЭКСГАУСТЕР 7. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 3',
#   'ЭКСГАУСТЕР 7. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 4',
#   'ЭКСГАУСТЕР 7. ВИБРАЦИЯ НА ОПОРЕ 2',
#   'ЭКСГАУСТЕР 7. ВИБРАЦИЯ НА ОПОРЕ 3',
#   'ЭКСГАУСТЕР 7. ВИБРАЦИЯ НА ОПОРЕ 4',
#   'ЭКСГАУСТЕР 7. ВИБРАЦИЯ НА ОПОРЕ 4. ПРОДОЛЬНАЯ.'],
#  'МАСЛЯНЫЙ ФИЛЬТР ЭКСГАУСТЕРА №7': ['ЭКСГАУСТЕР 7. ТОК РОТОРА 1',
#   'ЭКСГАУСТЕР 7. ТОК РОТОРА 2',
#   'ЭКСГАУСТЕР 7. ТОК СТАТОРА',
#   'ЭКСГАУСТЕР 7. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 2',
#   'ЭКСГАУСТЕР 7. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 3',
#   'ЭКСГАУСТЕР 7. ТЕМПЕРАТУРА МАСЛА В СИСТЕМЕ',
#   'ЭКСГАУСТЕР 7. ВИБРАЦИЯ НА ОПОРЕ 1',
#   'ЭКСГАУСТЕР 7. ВИБРАЦИЯ НА ОПОРЕ 2',
#   'ЭКСГАУСТЕР 7. ВИБРАЦИЯ НА ОПОРЕ 4. ПРОДОЛЬНАЯ.'],
#  'ТР-Р ТМ-4000-10/6 ЭКСГ. №7': [],
#  'ТСМТ-101-010-50М-200 ТЕРМОПР.ПОДШ.Т.3': [],
#  'ВК 310С ВИБРОПРЕОБРАЗОВАТЕЛЬ ЭКСГ.№7 Т.2': [],
#  'ВК 310С ВИБРОПРЕОБРАЗОВАТЕЛЬ ЭКСГ.№7 Т.4': [],
#  'ТИРИСТОРНЫЙ ВОЗБУДИТЕЛЬ ТВ-400 ЭКСГ7 ВУ1': ['ЭКСГАУСТЕР 7. ТОК СТАТОРА',
#   'ЭКСГАУСТЕР 7. ДАВЛЕНИЕ МАСЛА В СИСТЕМЕ',
#   'ЭКСГАУСТЕР 7. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 1',
#   'ЭКСГАУСТЕР 7. ВИБРАЦИЯ НА ОПОРЕ 1',
#   'ЭКСГАУСТЕР 7. ВИБРАЦИЯ НА ОПОРЕ 2',
#   'ЭКСГАУСТЕР 7. ВИБРАЦИЯ НА ОПОРЕ 4',
#   'ЭКСГАУСТЕР 7. ВИБРАЦИЯ НА ОПОРЕ 4. ПРОДОЛЬНАЯ.'],
#  'ТСМТ-101-010-50М-400 ТЕРМОПР.ПОДШ.Т.2': [],
#  'КЛ1 ТР№7 ДО ЭД ЭКСГАУСТЕРА №7': [],
#  'МЕТРАН-100 ДАТЧИКИ ДАВЛЕНИЯ ЭКСГ.№7': [],
#  'РЕГУЛИРУЮЩАЯ АППАРАТУРА ЭКСГАУСТЕРА №7': [],
#  'ЭЛ/ДВИГАТЕЛЬ ГАЗ. ЗАДВИЖКИ ЭКСГ. №7': [],
#  'ТСМТ-101-010-50М-400 ТЕРМОПР.ПОДШ.Т.1': []}

%%time
y_X_corr_d_7 = {}
y_X_imp_7_list = {}
for col in y_train_7.columns:
    (
        y_X_corr_d_7[col[20:]], 
        y_X_imp_7_list[col[20:]] 
    ) = compute_corr_target(dd_X_train_7, dd_y_train_7[col], 0.15)

Свернутый список:

In [778]:
hide_toggle()
# {'РОТОР ЭКСГ. №8': ['ЭКСГАУСТЕР 8. ТОК РОТОРА 1',
#   'ЭКСГАУСТЕР 8. ТОК РОТОРА 2',
#   'ЭКСГАУСТЕР 8. ТЕМПЕРАТУРА МАСЛА В МАСЛОБЛОКЕ',
#   'ЭКСГАУСТЕР 8. ВИБРАЦИЯ НА ОПОРЕ 1'],
#  'ЭЛЕКТРОДВИГАТЕЛЬ ДСПУ-140-84-4 ЭКСГ. №8': ['ЭКСГАУСТЕР 8. ТОК РОТОРА 1',
#   'ЭКСГАУСТЕР 8. ТОК РОТОРА 2',
#   'ЭКСГАУСТЕР 8. ТОК СТАТОРА',
#   'ЭКСГАУСТЕР 8. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 1',
#   'ЭКСГАУСТЕР 8. ТЕМПЕРАТУРА МАСЛА В СИСТЕМЕ',
#   'ЭКСГАУСТЕР 8. ВИБРАЦИЯ НА ОПОРЕ 1',
#   'ЭКСГАУСТЕР 8. ВИБРАЦИЯ НА ОПОРЕ 2',
#   'ЭКСГАУСТЕР 8. ВИБРАЦИЯ НА ОПОРЕ 4. ПРОДОЛЬНАЯ.'],
#  'КОРПУС ЭКСГ. №8': ['ЭКСГАУСТЕР 8. ВИБРАЦИЯ НА ОПОРЕ 1',
#   'ЭКСГАУСТЕР 8. ВИБРАЦИЯ НА ОПОРЕ 3',
#   'ЭКСГАУСТЕР 8. ВИБРАЦИЯ НА ОПОРЕ 4'],
#  'РЕДУКТОР ГАЗ. ЗАДВИЖКИ ЭКСГ. №8': ['ЭКСГАУСТЕР 8. ТОК РОТОРА 1',
#   'ЭКСГАУСТЕР 8. ТОК РОТОРА 2',
#   'ЭКСГАУСТЕР 8. ТОК СТАТОРА',
#   'ЭКСГАУСТЕР 8. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 1',
#   'ЭКСГАУСТЕР 8. ТЕМПЕРАТУРА МАСЛА В МАСЛОБЛОКЕ',
#   'ЭКСГАУСТЕР 8. ВИБРАЦИЯ НА ОПОРЕ 1',
#   'ЭКСГАУСТЕР 8. ВИБРАЦИЯ НА ОПОРЕ 4. ПРОДОЛЬНАЯ.'],
#  'ВК 310С ВИБРОПРЕОБРАЗОВАТЕЛЬ ЭКСГ.№8 Т.3': ['ЭКСГАУСТЕР 8. ТОК РОТОРА 1',
#   'ЭКСГАУСТЕР 8. ТОК РОТОРА 2',
#   'ЭКСГАУСТЕР 8. ТОК СТАТОРА',
#   'ЭКСГАУСТЕР 8. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 2',
#   'ЭКСГАУСТЕР 8. ТЕМПЕРАТУРА МАСЛА В МАСЛОБЛОКЕ',
#   'ЭКСГАУСТЕР 8. ВИБРАЦИЯ НА ОПОРЕ 2',
#   'ЭКСГАУСТЕР 8. ВИБРАЦИЯ НА ОПОРЕ 3. ПРОДОЛЬНАЯ.'],
#  'ВК 310С ВИБРОПРЕОБРАЗОВАТЕЛЬ ЭКСГ.№8 Т.4': ['ЭКСГАУСТЕР 8. ТОК РОТОРА 1',
#   'ЭКСГАУСТЕР 8. ТОК РОТОРА 2',
#   'ЭКСГАУСТЕР 8. ТОК СТАТОРА',
#   'ЭКСГАУСТЕР 8. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 1',
#   'ЭКСГАУСТЕР 8. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 2',
#   'ЭКСГАУСТЕР 8. ТЕМПЕРАТУРА МАСЛА В СИСТЕМЕ',
#   'ЭКСГАУСТЕР 8. ТЕМПЕРАТУРА МАСЛА В МАСЛОБЛОКЕ',
#   'ЭКСГАУСТЕР 8. ВИБРАЦИЯ НА ОПОРЕ 2',
#   'ЭКСГАУСТЕР 8. ВИБРАЦИЯ НА ОПОРЕ 3. ПРОДОЛЬНАЯ.',
#   'ЭКСГАУСТЕР 8. ВИБРАЦИЯ НА ОПОРЕ 4. ПРОДОЛЬНАЯ.'],
#  'ЭЛ/ДВИГАТЕЛЬ ГАЗ. ЗАДВИЖКИ ЭКСГ. №8': [],
#  'МАСЛООХЛАДИТЕЛЬ  М-05-1 ЭКСГ. №8': ['ЭКСГАУСТЕР 8. ТОК РОТОРА 1',
#   'ЭКСГАУСТЕР 8. ТОК РОТОРА 2',
#   'ЭКСГАУСТЕР 8. ВИБРАЦИЯ НА ОПОРЕ 1',
#   'ЭКСГАУСТЕР 8. ВИБРАЦИЯ НА ОПОРЕ 2',
#   'ЭКСГАУСТЕР 8. ВИБРАЦИЯ НА ОПОРЕ 3. ПРОДОЛЬНАЯ.'],
#  'ТИРИСТОРНЫЙ ВОЗБУДИТЕЛЬ СПВД-М10-400-5': [],
#  'КЛ2 ТР№8 ДО ЭД ЭКСГАУСТЕРА №8': ['ЭКСГАУСТЕР 8. ТОК РОТОРА 1',
#   'ЭКСГАУСТЕР 8. ТОК РОТОРА 2',
#   'ЭКСГАУСТЕР 8. ДАВЛЕНИЕ МАСЛА В СИСТЕМЕ',
#   'ЭКСГАУСТЕР 8. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 2',
#   'ЭКСГАУСТЕР 8. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 4',
#   'ЭКСГАУСТЕР 8. ТЕМПЕРАТУРА МАСЛА В СИСТЕМЕ',
#   'ЭКСГАУСТЕР 8. ВИБРАЦИЯ НА ОПОРЕ 3',
#   'ЭКСГАУСТЕР 8. ВИБРАЦИЯ НА ОПОРЕ 3. ПРОДОЛЬНАЯ.',
#   'ЭКСГАУСТЕР 8. ВИБРАЦИЯ НА ОПОРЕ 4'],
#  'КЛ1 ТР№8 ДО ЭД ЭКСГАУСТЕРА №8': ['ЭКСГАУСТЕР 8. ТОК РОТОРА 1',
#   'ЭКСГАУСТЕР 8. ТОК РОТОРА 2',
#   'ЭКСГАУСТЕР 8. ДАВЛЕНИЕ МАСЛА В СИСТЕМЕ',
#   'ЭКСГАУСТЕР 8. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 2',
#   'ЭКСГАУСТЕР 8. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 4',
#   'ЭКСГАУСТЕР 8. ТЕМПЕРАТУРА МАСЛА В СИСТЕМЕ',
#   'ЭКСГАУСТЕР 8. ВИБРАЦИЯ НА ОПОРЕ 3',
#   'ЭКСГАУСТЕР 8. ВИБРАЦИЯ НА ОПОРЕ 3. ПРОДОЛЬНАЯ.',
#   'ЭКСГАУСТЕР 8. ВИБРАЦИЯ НА ОПОРЕ 4'],
#  'ТСМТ-101-010-50М-400 ТЕРМОПР.ПОДШ.Т.2': [],
#  'КОЖУХ МУФТЫ ЭКСГ. №8': ['ЭКСГАУСТЕР 8. ТОК РОТОРА 1',
#   'ЭКСГАУСТЕР 8. ТОК РОТОРА 2',
#   'ЭКСГАУСТЕР 8. ТОК СТАТОРА',
#   'ЭКСГАУСТЕР 8. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 1',
#   'ЭКСГАУСТЕР 8. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 2',
#   'ЭКСГАУСТЕР 8. ТЕМПЕРАТУРА МАСЛА В МАСЛОБЛОКЕ',
#   'ЭКСГАУСТЕР 8. ВИБРАЦИЯ НА ОПОРЕ 2',
#   'ЭКСГАУСТЕР 8. ВИБРАЦИЯ НА ОПОРЕ 3. ПРОДОЛЬНАЯ.'],
#  'ГСМ ЭКСГ. №8': ['ЭКСГАУСТЕР 8. ТОК РОТОРА 1',
#   'ЭКСГАУСТЕР 8. ТОК РОТОРА 2',
#   'ЭКСГАУСТЕР 8. ТОК СТАТОРА',
#   'ЭКСГАУСТЕР 8. ДАВЛЕНИЕ МАСЛА В СИСТЕМЕ',
#   'ЭКСГАУСТЕР 8. ТЕМПЕРАТУРА МАСЛА В СИСТЕМЕ',
#   'ЭКСГАУСТЕР 8. ВИБРАЦИЯ НА ОПОРЕ 2'],
#  'ПОДШИПНИК ОПОРНЫЙ №2': ['ЭКСГАУСТЕР 8. ТОК РОТОРА 1',
#   'ЭКСГАУСТЕР 8. ТОК РОТОРА 2',
#   'ЭКСГАУСТЕР 8. ТОК СТАТОРА',
#   'ЭКСГАУСТЕР 8. ТЕМПЕРАТУРА МАСЛА В МАСЛОБЛОКЕ',
#   'ЭКСГАУСТЕР 8. ВИБРАЦИЯ НА ОПОРЕ 1',
#   'ЭКСГАУСТЕР 8. ВИБРАЦИЯ НА ОПОРЕ 3. ПРОДОЛЬНАЯ.',
#   'ЭКСГАУСТЕР 8. ВИБРАЦИЯ НА ОПОРЕ 4. ПРОДОЛЬНАЯ.'],
#  'ЭКСГАУСТЕР А/М №8': [],
#  'ЗАПОРНАЯ АРМАТУРА ЭКСГАУСТЕРА №8': ['ЭКСГАУСТЕР 8. ВИБРАЦИЯ НА ОПОРЕ 1',
#   'ЭКСГАУСТЕР 8. ВИБРАЦИЯ НА ОПОРЕ 4. ПРОДОЛЬНАЯ.'],
#  'ТСМТ-101-010-50М-200 ТЕРМОПР.ПОДШ.Т.4': [],
#  'МАСЛЯНЫЙ ФИЛЬТР ЭКСГАУСТЕРА №8': [],
#  'ТИРИСТОРНЫЙ ВОЗБУДИТЕЛЬ ТВ-400 ЭКСГ8 ВУ1': [],
#  'ПОДШИПНИК ОПОРНЫЙ №1': [],
#  'ЭЛЕКТРООБОРУДОВАНИЯ ЭКСГАУСТЕРА №8': [],
#  'ПОДШИПНИК ОПОРНЫЙ ЭКСГ. №8': ['ЭКСГАУСТЕР 8. ТОК РОТОРА 1',
#   'ЭКСГАУСТЕР 8. ТОК РОТОРА 2',
#   'ЭКСГАУСТЕР 8. ТОК СТАТОРА',
#   'ЭКСГАУСТЕР 8. ДАВЛЕНИЕ МАСЛА В СИСТЕМЕ',
#   'ЭКСГАУСТЕР 8. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 1',
#   'ЭКСГАУСТЕР 8. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 3',
#   'ЭКСГАУСТЕР 8. ТЕМПЕРАТУРА МАСЛА В СИСТЕМЕ',
#   'ЭКСГАУСТЕР 8. ВИБРАЦИЯ НА ОПОРЕ 1',
#   'ЭКСГАУСТЕР 8. ВИБРАЦИЯ НА ОПОРЕ 2',
#   'ЭКСГАУСТЕР 8. ВИБРАЦИЯ НА ОПОРЕ 4',
#   'ЭКСГАУСТЕР 8. ВИБРАЦИЯ НА ОПОРЕ 4. ПРОДОЛЬНАЯ.'],
#  'ЗАДВИЖКА ЭКСГ. №8': ['ЭКСГАУСТЕР 8. ТОК РОТОРА 1',
#   'ЭКСГАУСТЕР 8. ТОК РОТОРА 2',
#   'ЭКСГАУСТЕР 8. ТОК СТАТОРА',
#   'ЭКСГАУСТЕР 8. ТЕМПЕРАТУРА МАСЛА В СИСТЕМЕ',
#   'ЭКСГАУСТЕР 8. ВИБРАЦИЯ НА ОПОРЕ 1',
#   'ЭКСГАУСТЕР 8. ВИБРАЦИЯ НА ОПОРЕ 2',
#   'ЭКСГАУСТЕР 8. ВИБРАЦИЯ НА ОПОРЕ 4',
#   'ЭКСГАУСТЕР 8. ВИБРАЦИЯ НА ОПОРЕ 4. ПРОДОЛЬНАЯ.'],
#  'МАСЛОНАСОС РАБОЧИЙ ЭКСГ. №8': ['ЭКСГАУСТЕР 8. ТОК РОТОРА 1',
#   'ЭКСГАУСТЕР 8. ТОК РОТОРА 2',
#   'ЭКСГАУСТЕР 8. ТОК СТАТОРА',
#   'ЭКСГАУСТЕР 8. ДАВЛЕНИЕ МАСЛА В СИСТЕМЕ',
#   'ЭКСГАУСТЕР 8. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 4',
#   'ЭКСГАУСТЕР 8. ТЕМПЕРАТУРА МАСЛА В МАСЛОБЛОКЕ',
#   'ЭКСГАУСТЕР 8. ВИБРАЦИЯ НА ОПОРЕ 1',
#   'ЭКСГАУСТЕР 8. ВИБРАЦИЯ НА ОПОРЕ 3',
#   'ЭКСГАУСТЕР 8. ВИБРАЦИЯ НА ОПОРЕ 4. ПРОДОЛЬНАЯ.'],
#  'МАСЛОНАСОС ШЕСТЕРЕНЧАТЫЙ (РЕЗ.) ЭКСГ. №8': ['ЭКСГАУСТЕР 8. ТОК РОТОРА 1',
#   'ЭКСГАУСТЕР 8. ТОК РОТОРА 2',
#   'ЭКСГАУСТЕР 8. ТОК СТАТОРА',
#   'ЭКСГАУСТЕР 8. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 4',
#   'ЭКСГАУСТЕР 8. ТЕМПЕРАТУРА МАСЛА В МАСЛОБЛОКЕ',
#   'ЭКСГАУСТЕР 8. ВИБРАЦИЯ НА ОПОРЕ 1',
#   'ЭКСГАУСТЕР 8. ВИБРАЦИЯ НА ОПОРЕ 4. ПРОДОЛЬНАЯ.'],
#  'МАСЛОНАСОС ШЕСТЕРЕНЧАТЫЙ (ПУСК.) ЭКСГ.№8': ['ЭКСГАУСТЕР 8. ТОК РОТОРА 1',
#   'ЭКСГАУСТЕР 8. ТОК РОТОРА 2',
#   'ЭКСГАУСТЕР 8. ТОК СТАТОРА',
#   'ЭКСГАУСТЕР 8. ДАВЛЕНИЕ МАСЛА В СИСТЕМЕ',
#   'ЭКСГАУСТЕР 8. ТЕМПЕРАТУРА МАСЛА В МАСЛОБЛОКЕ',
#   'ЭКСГАУСТЕР 8. ВИБРАЦИЯ НА ОПОРЕ 3',
#   'ЭКСГАУСТЕР 8. ВИБРАЦИЯ НА ОПОРЕ 3. ПРОДОЛЬНАЯ.',
#   'ЭКСГАУСТЕР 8. ВИБРАЦИЯ НА ОПОРЕ 4'],
#  'ВК 310С ВИБРОПРЕОБРАЗОВАТЕЛЬ ЭКСГ.№8 Т.2': [],
#  'ТР-Р ТМ-6300-10/6 ЭКСГ. №8': ['ЭКСГАУСТЕР 8. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 1',
#   'ЭКСГАУСТЕР 8. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 3',
#   'ЭКСГАУСТЕР 8. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 4',
#   'ЭКСГАУСТЕР 8. ТЕМПЕРАТУРА МАСЛА В СИСТЕМЕ'],
#  'ПОДШИПНИК ОПОРНО-УПОРНЫЙ ЭКСГ. №8': ['ЭКСГАУСТЕР 8. ТОК РОТОРА 1',
#   'ЭКСГАУСТЕР 8. ТОК РОТОРА 2',
#   'ЭКСГАУСТЕР 8. ТОК СТАТОРА',
#   'ЭКСГАУСТЕР 8. ДАВЛЕНИЕ МАСЛА В СИСТЕМЕ',
#   'ЭКСГАУСТЕР 8. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 2',
#   'ЭКСГАУСТЕР 8. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 4',
#   'ЭКСГАУСТЕР 8. ТЕМПЕРАТУРА МАСЛА В МАСЛОБЛОКЕ',
#   'ЭКСГАУСТЕР 8. ВИБРАЦИЯ НА ОПОРЕ 1',
#   'ЭКСГАУСТЕР 8. ВИБРАЦИЯ НА ОПОРЕ 4. ПРОДОЛЬНАЯ.'],
#  'МАСЛОПРОВОДЫ ЭКСГАУСТЕРА №8': ['ЭКСГАУСТЕР 8. ТОК РОТОРА 1',
#   'ЭКСГАУСТЕР 8. ТОК РОТОРА 2',
#   'ЭКСГАУСТЕР 8. ТЕМПЕРАТУРА МАСЛА В СИСТЕМЕ']}

%%time
y_X_corr_d_8 = {}
y_X_imp_8_list = {}
for col in y_train_8.columns:
    (
        y_X_corr_d_8[col[20:]], 
        y_X_imp_8_list[col[20:]] 
    ) = compute_corr_target(dd_X_train_8, dd_y_train_8[col], 0.15)

Свернутый список:

In [779]:
hide_toggle()
# {'ЗАПОРНАЯ АРМАТУРА ЭКСГАУСТЕРА №9': ['ЭКСГАУСТЕР 9. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 2',
#   'ЭКСГАУСТЕР 9. ВИБРАЦИЯ НА ОПОРЕ 2'],
#  'МАСЛОСТАНЦИЯ ЖИДКОЙ СМАЗКИ ЭКСГ. №9': ['ЭКСГАУСТЕР 9. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 2',
#   'ЭКСГАУСТЕР 9. ВИБРАЦИЯ НА ОПОРЕ 2'],
#  'ЭЛЕКТРОАППАРАТУРА ЭКСГ. №9': [],
#  'КЛ1 ТР№9 ДО ЭД ЭКСГАУСТЕРА №9': [],
#  'ЭЛЕКТРОДВИГАТЕЛЬ ДСПУ-140-84-4 ЭКСГ. №9': ['ЭКСГАУСТЕР 9. ТОК РОТОРА 1',
#   'ЭКСГАУСТЕР 9. ТОК РОТОРА 2',
#   'ЭКСГАУСТЕР 9. ТОК СТАТОРА',
#   'ЭКСГАУСТЕР 9. ДАВЛЕНИЕ МАСЛА В СИСТЕМЕ',
#   'ЭКСГАУСТЕР 9. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 1',
#   'ЭКСГАУСТЕР 9. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 2',
#   'ЭКСГАУСТЕР 9. ВИБРАЦИЯ НА ОПОРЕ 1'],
#  'КОРПУС ЭКСГ. №9': ['ЭКСГАУСТЕР 9. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 1',
#   'ЭКСГАУСТЕР 9. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 2',
#   'ЭКСГАУСТЕР 9. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 4',
#   'ЭКСГАУСТЕР 9. ТЕМПЕРАТУРА МАСЛА В МАСЛОБЛОКЕ',
#   'ЭКСГАУСТЕР 9. ВИБРАЦИЯ НА ОПОРЕ 1',
#   'ЭКСГАУСТЕР 9. ВИБРАЦИЯ НА ОПОРЕ 3. ПРОДОЛЬНАЯ.',
#   'ЭКСГАУСТЕР 9. ВИБРАЦИЯ НА ОПОРЕ 4',
#   'ЭКСГАУСТЕР 9. ВИБРАЦИЯ НА ОПОРЕ 4. ПРОДОЛЬНАЯ.'],
#  'РЕДУКТОР ГАЗ. ЗАДВИЖКИ ЭКСГ. №9': ['ЭКСГАУСТЕР 9. ТОК РОТОРА 1',
#   'ЭКСГАУСТЕР 9. ТОК РОТОРА 2',
#   'ЭКСГАУСТЕР 9. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 2',
#   'ЭКСГАУСТЕР 9. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 3',
#   'ЭКСГАУСТЕР 9. ТЕМПЕРАТУРА МАСЛА В СИСТЕМЕ',
#   'ЭКСГАУСТЕР 9. ТЕМПЕРАТУРА МАСЛА В МАСЛОБЛОКЕ',
#   'ЭКСГАУСТЕР 9. ВИБРАЦИЯ НА ОПОРЕ 1',
#   'ЭКСГАУСТЕР 9. ВИБРАЦИЯ НА ОПОРЕ 2',
#   'ЭКСГАУСТЕР 9. ВИБРАЦИЯ НА ОПОРЕ 3',
#   'ЭКСГАУСТЕР 9. ВИБРАЦИЯ НА ОПОРЕ 4',
#   'ЭКСГАУСТЕР 9. ВИБРАЦИЯ НА ОПОРЕ 4. ПРОДОЛЬНАЯ.'],
#  'МАСЛООХЛАДИТЕЛЬ  М-05-1 ЭКСГ. №9': ['ЭКСГАУСТЕР 9. ТОК РОТОРА 1',
#   'ЭКСГАУСТЕР 9. ТОК РОТОРА 2',
#   'ЭКСГАУСТЕР 9. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 1',
#   'ЭКСГАУСТЕР 9. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 2',
#   'ЭКСГАУСТЕР 9. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 3',
#   'ЭКСГАУСТЕР 9. ТЕМПЕРАТУРА МАСЛА В СИСТЕМЕ',
#   'ЭКСГАУСТЕР 9. ТЕМПЕРАТУРА МАСЛА В МАСЛОБЛОКЕ',
#   'ЭКСГАУСТЕР 9. ВИБРАЦИЯ НА ОПОРЕ 1',
#   'ЭКСГАУСТЕР 9. ВИБРАЦИЯ НА ОПОРЕ 4'],
#  'ЭЛ/ДВИГАТЕЛЬ ГАЗ. ЗАДВИЖКИ ЭКСГ. №9': [],
#  'ЭЛЕКТРООБОРУДОВАНИЯ ЭКСГАУСТЕРА №9': ['ЭКСГАУСТЕР 9. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 2',
#   'ЭКСГАУСТЕР 9. ВИБРАЦИЯ НА ОПОРЕ 1',
#   'ЭКСГАУСТЕР 9. ВИБРАЦИЯ НА ОПОРЕ 3',
#   'ЭКСГАУСТЕР 9. ВИБРАЦИЯ НА ОПОРЕ 4',
#   'ЭКСГАУСТЕР 9. ВИБРАЦИЯ НА ОПОРЕ 4. ПРОДОЛЬНАЯ.'],
#  'ПОДШИПНИК ОПОРНО-УПОРНЫЙ ЭКСГ. №9': ['ЭКСГАУСТЕР 9. ТОК РОТОРА 1',
#   'ЭКСГАУСТЕР 9. ТОК РОТОРА 2',
#   'ЭКСГАУСТЕР 9. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 1',
#   'ЭКСГАУСТЕР 9. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 2',
#   'ЭКСГАУСТЕР 9. ТЕМПЕРАТУРА МАСЛА В МАСЛОБЛОКЕ',
#   'ЭКСГАУСТЕР 9. ВИБРАЦИЯ НА ОПОРЕ 1',
#   'ЭКСГАУСТЕР 9. ВИБРАЦИЯ НА ОПОРЕ 2',
#   'ЭКСГАУСТЕР 9. ВИБРАЦИЯ НА ОПОРЕ 4'],
#  'РОТОР ЭКСГ. №9': ['ЭКСГАУСТЕР 9. ДАВЛЕНИЕ МАСЛА В СИСТЕМЕ',
#   'ЭКСГАУСТЕР 9. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 1',
#   'ЭКСГАУСТЕР 9. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 2',
#   'ЭКСГАУСТЕР 9. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 3',
#   'ЭКСГАУСТЕР 9. ТЕМПЕРАТУРА МАСЛА В МАСЛОБЛОКЕ',
#   'ЭКСГАУСТЕР 9. ВИБРАЦИЯ НА ОПОРЕ 1',
#   'ЭКСГАУСТЕР 9. ВИБРАЦИЯ НА ОПОРЕ 3. ПРОДОЛЬНАЯ.',
#   'ЭКСГАУСТЕР 9. ВИБРАЦИЯ НА ОПОРЕ 4'],
#  'ТР-Р ТМ-6300-10/6 ЭКСГ. №9': ['ЭКСГАУСТЕР 9. ТОК РОТОРА 1',
#   'ЭКСГАУСТЕР 9. ТОК РОТОРА 2',
#   'ЭКСГАУСТЕР 9. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 1',
#   'ЭКСГАУСТЕР 9. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 2',
#   'ЭКСГАУСТЕР 9. ТЕМПЕРАТУРА МАСЛА В СИСТЕМЕ',
#   'ЭКСГАУСТЕР 9. ВИБРАЦИЯ НА ОПОРЕ 1',
#   'ЭКСГАУСТЕР 9. ВИБРАЦИЯ НА ОПОРЕ 2',
#   'ЭКСГАУСТЕР 9. ВИБРАЦИЯ НА ОПОРЕ 3',
#   'ЭКСГАУСТЕР 9. ВИБРАЦИЯ НА ОПОРЕ 3. ПРОДОЛЬНАЯ.',
#   'ЭКСГАУСТЕР 9. ВИБРАЦИЯ НА ОПОРЕ 4',
#   'ЭКСГАУСТЕР 9. ВИБРАЦИЯ НА ОПОРЕ 4. ПРОДОЛЬНАЯ.'],
#  'ПОДШИПНИК ОПОРНЫЙ ЭКСГ. №9': ['ЭКСГАУСТЕР 9. ДАВЛЕНИЕ МАСЛА В СИСТЕМЕ',
#   'ЭКСГАУСТЕР 9. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 1',
#   'ЭКСГАУСТЕР 9. ТЕМПЕРАТУРА МАСЛА В СИСТЕМЕ',
#   'ЭКСГАУСТЕР 9. ВИБРАЦИЯ НА ОПОРЕ 1',
#   'ЭКСГАУСТЕР 9. ВИБРАЦИЯ НА ОПОРЕ 3',
#   'ЭКСГАУСТЕР 9. ВИБРАЦИЯ НА ОПОРЕ 3. ПРОДОЛЬНАЯ.'],
#  'МАСЛОНАСОС РАБОЧИЙ ЭКСГ. №9': ['ЭКСГАУСТЕР 9. ТОК РОТОРА 1',
#   'ЭКСГАУСТЕР 9. ТОК РОТОРА 2',
#   'ЭКСГАУСТЕР 9. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 1',
#   'ЭКСГАУСТЕР 9. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 2',
#   'ЭКСГАУСТЕР 9. ТЕМПЕРАТУРА МАСЛА В МАСЛОБЛОКЕ',
#   'ЭКСГАУСТЕР 9. ВИБРАЦИЯ НА ОПОРЕ 1',
#   'ЭКСГАУСТЕР 9. ВИБРАЦИЯ НА ОПОРЕ 4',
#   'ЭКСГАУСТЕР 9. ВИБРАЦИЯ НА ОПОРЕ 4. ПРОДОЛЬНАЯ.'],
#  'ПОДШИПНИК ОПОРНЫЙ №2': ['ЭКСГАУСТЕР 9. ДАВЛЕНИЕ МАСЛА В СИСТЕМЕ',
#   'ЭКСГАУСТЕР 9. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 1',
#   'ЭКСГАУСТЕР 9. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 2',
#   'ЭКСГАУСТЕР 9. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 3',
#   'ЭКСГАУСТЕР 9. ТЕМПЕРАТУРА МАСЛА В МАСЛОБЛОКЕ',
#   'ЭКСГАУСТЕР 9. ВИБРАЦИЯ НА ОПОРЕ 3. ПРОДОЛЬНАЯ.'],
#  'ГСМ ЭКСГ. №9': ['ЭКСГАУСТЕР 9. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 2',
#   'ЭКСГАУСТЕР 9. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 4',
#   'ЭКСГАУСТЕР 9. ВИБРАЦИЯ НА ОПОРЕ 4'],
#  'КОЖУХ МУФТЫ ЭКСГ. №9': ['ЭКСГАУСТЕР 9. ТОК РОТОРА 1',
#   'ЭКСГАУСТЕР 9. ТОК РОТОРА 2',
#   'ЭКСГАУСТЕР 9. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 2',
#   'ЭКСГАУСТЕР 9. ТЕМПЕРАТУРА МАСЛА В СИСТЕМЕ',
#   'ЭКСГАУСТЕР 9. ВИБРАЦИЯ НА ОПОРЕ 1'],
#  'ПОДШИПНИК ОПОРНЫЙ №1': ['ЭКСГАУСТЕР 9. ТОК РОТОРА 1',
#   'ЭКСГАУСТЕР 9. ТОК РОТОРА 2',
#   'ЭКСГАУСТЕР 9. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 1',
#   'ЭКСГАУСТЕР 9. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 2',
#   'ЭКСГАУСТЕР 9. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 3',
#   'ЭКСГАУСТЕР 9. ТЕМПЕРАТУРА МАСЛА В СИСТЕМЕ',
#   'ЭКСГАУСТЕР 9. ВИБРАЦИЯ НА ОПОРЕ 2',
#   'ЭКСГАУСТЕР 9. ВИБРАЦИЯ НА ОПОРЕ 4'],
#  'ЗАДВИЖКА ЭКСГ. №9': ['ЭКСГАУСТЕР 9. ДАВЛЕНИЕ МАСЛА В СИСТЕМЕ',
#   'ЭКСГАУСТЕР 9. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 1',
#   'ЭКСГАУСТЕР 9. ТЕМПЕРАТУРА МАСЛА В СИСТЕМЕ',
#   'ЭКСГАУСТЕР 9. ВИБРАЦИЯ НА ОПОРЕ 1'],
#  'ВК 310С ВИБРОПРЕОБРАЗОВАТЕЛЬ ЭКСГ.№9 Т.1': [],
#  'МАСЛОПРОВОДЫ ЭКСГАУСТЕРА №9': [],
#  'ТИРИСТОРНЫЙ ВОЗБУДИТЕЛЬ ТВ-400 ЭКСГ9 ВУ1': [],
#  'МЕТРАН-100 ДАТЧИКИ ДАВЛЕНИЯ ЭКСГ.№9': [],
#  'ТСМТ-101-010-50М-80 ТЕРМОПРЕОБР.МАСЛО': [],
#  'ТСМТ-101-010-50М-400 ТЕРМОПР.ПОДШ.Т.1': [],
#  'ЭКСГАУСТЕР А/М №9': [],
#  'ДВИГАТЕЛЬ ПУСКОВОГО МАСЛОНАСОСА ЭКСГ. №9': []}

%%time
y_X_corr_d_9 = {}
y_X_imp_9_list = {}
for col in y_train_9.columns:
    (
        y_X_corr_d_9[col[20:]], 
        y_X_imp_9_list[col[20:]] 
    ) = compute_corr_target(dd_X_train_9, dd_y_train_9[col], 0.15)

### Работа с пропусками<a class="anchor" id="section_3_5"></a>

### Графики<a class="anchor" id="section_3_6"></a>

In [735]:
X_train_4 = dd_X_train_4.compute()
cols = X_train_4.columns
res_df = X_train_4.resample('1D').mean().interpolate()

In [736]:
for i in range(len(cols)):
    fig = go.Figure(data=[go.Scatter(y=res_df[cols[i]], x=res_df[cols[i]].index)])
    fig.update_layout(title_text= f'{i} ' + cols[i][14:], width=1300, height=400)
    fig.show()

На графикав видны провалы, нерегулярные и не одинаковые для каждого параметра. Вомзожно, они происходили из-за поломок\
Вибрация на опоре 3(12) нечто похожее на периодические подъемы и резкие падения

In [ ]:
y_train_4.resample('1H').max()['2019-03-31  00:00:00' : '2019-04-5  00:10:00']

Наприме, ток ротора 01.04.2019. В это время действительно были незначительные поломки

In [ ]:
for i in range(len(cols)):
    fig = go.Figure()
    fig.add_trace(go.Histogram(name='2019', x=res_df[cols[i]]['2019-01-18  00:00:00':'2019-12-31  00:10:00'], opacity=0.75))
    fig.add_trace(go.Histogram(name='2020', x=res_df[cols[i]]['2020-01-01  00:00:00':'2020-12-31  00:10:00'], opacity=0.75))
    fig.add_trace(go.Histogram(name='2021', x=res_df[cols[i]]['2021-01-01  00:00:00':'2021-12-31  00:10:00'], opacity=0.75))
    fig.update_layout(title_text= f'{i} ' + cols[i][14:],barmode='overlay')
    fig.show()

По ежегодным распределениям видно, что где-то в 2020 году произошел переход на другой режим работы, и распределения поменялись. Вибрация на опоре 3 обращает себя внимание резкими аномалиями. В вибрацию на опоре 4 попали отрицательные значения, это явная ошибка

In [ ]:
X_train_4[X_train_4[cols[14]] < 0]

 23 декабря произошла данная аномалия

In [ ]:
y_train_4['2019-12-23 10:30:40' : '2019-12-24 10:33:00'].resample('30Min').mean()

При этом серьезных поломок на оборудовании не появилось, скорее всего проблема в датчиках

In [744]:
for i in range(len(cols)):
    fig = go.Figure()
    fig.add_trace(go.Histogram(name='2019-20', x=res_df[cols[i]]['2019-01-18  00:00:00':'2020-08-01  00:10:00'], opacity=0.75))
    fig.add_trace(go.Histogram(name='2020-21', x=res_df[cols[i]]['2020-08-01  00:00:00':'2021-12-31  00:10:00'], opacity=0.75))
    fig.update_layout(title_text= f'{i} ' + cols[i][14:],barmode='overlay')
    fig.show()

В целом отчетливо различаются изменения распределения части параметров по этим двум периодам, хотя некоторые параметры не меняли свое распределение

In [ ]:
del X_train_4, cols, res_df, y_train_4

**Эксгаустер 5**

In [ ]:
X_train_5 = dd_X_train_5.compute()
cols = X_train_5.columns
res_df = X_train_5.resample('1D').mean().interpolate()

In [ ]:
for i in range(len(cols)):
    fig = go.Figure(data=[go.Scatter(y=res_df[cols[i]], x=res_df[cols[i]].index)])
    fig.update_layout(title_text= f'{i} ' + cols[i][14:], width=1300, height=400)
    fig.show()

В 2019 ток статора(2) имел множество заметных выбросов, большинство из которых держалось как раз до середины 2020. В вибрации на опоре(10) снова явный отрицательный выброс 28 апреля.\
У вбирации на опоре 3(12) с начала и до конца августа поднималась величина. Вообще в вибрациях эти резкие подъемы и обрывы, нужно проверить связь с поломками

In [ ]:
for i in range(len(cols)):
    fig = go.Figure()
    fig.add_trace(go.Histogram(name='2019-20', x=res_df[cols[i]]['2019-01-18  00:00:00':'2020-08-01  00:10:00'], opacity=0.75))
    fig.add_trace(go.Histogram(name='2020-21', x=res_df[cols[i]]['2020-08-01  00:00:00':'2021-12-31  00:10:00'], opacity=0.75))
    fig.update_layout(title_text= f'{i} ' + cols[i][14:],barmode='overlay')
    fig.show()

Снова есть различия в распределениях по этим периодам, но не такие значительные

In [ ]:
del X_train_5, cols, res_df

**Основная информация о колонках X_train: сезонная декомпозиция**<a class="anchor" id="sub_section_3_6_3"></a>

In [783]:
def plot_seasonality(df, start, end, res):
    """
    Вывод временных зависимостей для отдельного параметра

    Аргументы:
        df(pd.Series): Исследуемый столбец.
        start(str): Начало временного отрезка.
        end(str): Окончание временного отрезка.
        res(str): Период для ресемплинга
        
    Вывод:
        fig: График.
    """
    print(f'Сезонный график для парметра {df.name} на промежутке от {start} до {end}:')
    print('')
    result = seasonal_decompose(df.resample(res).mean()[start:end].interpolate())
    fig = make_subplots(
        rows=4, cols=1,
        subplot_titles=["Observed", "Trend", "Seasonal", "Residuals"])
    fig.add_trace(
        go.Scatter(x=result.seasonal.index, y=result.observed, mode='lines'),
            row=1, col=1,
        )

    fig.add_trace(
        go.Scatter(x=result.trend.index, y=result.trend, mode='lines'),
            row=2, col=1,
        )

    fig.add_trace(
        go.Scatter(x=result.seasonal.index, y=result.seasonal, mode='lines'),
            row=3, col=1,
        )

    fig.add_trace(
        go.Scatter(x=result.resid.index, y=result.resid, mode='lines'),
            row=4, col=1,
        )
    fig['layout']['yaxis4'].update(visible=False)
    fig.update_layout(
                height=900, margin=dict(t=100), title_x=0.5, showlegend=False,
                title_text=f'{df.name}'
            )
    return fig

In [784]:
plot_seasonality(X_train_4[X_train_4.columns[4]], '2019-01-18  00:00:00', '2019-01-21  23:55:00', '1H')

Сезонный график для парметра ЭКСГАУСТЕР 4. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 1 на промежутке от 2019-01-18  00:00:00 до 2019-01-21  23:55:00:



При ресамплинге в 1 час можно наблюдать ежедневную сезонность, в 1 день - еженедельную, а в 15 дней -- ежегодную. Так, резкий пик работы приходится на середину июля, а спад на конец ноября

In [ ]:
del X_train_4
X_train_5 = dd_X_train_5.compute()
cols = X_train_5.columns

In [ ]:
plot_seasonality(X_train_5[cols[0]], '2019-01-18  00:00:00', '2019-12-19  23:55:00', '1H')

У 5ого эксгаустера практически незаметная ежегодная сезонность, а вот ежедневная и еженедельная четко прослеживается

In [ ]:
del X_train_5

## Формирование выборок для моделей<a class="anchor" id="chapter4"></a>

**Скользящее окно?**

Создадим разные выборки и сравним результаты модели:
- Ресемплирование по часу с простой интерполяцией
- Ресемплирование по 5 минут с простой интерполяцией для разных временных отрезков
- Умное заполнение пропусков
- Мультиклассификация

In [7]:
X_train_4 = dd_X_train_4.compute()
y_train_4 = dd_y_train_4.compute()

Создадим столбцы для м1 и м3 отдельно:

In [8]:
y_train_m3 = y_train_4.replace(1, 0)
y_train_m3 = y_train_m3.replace(2, 1)
y_train_m1 = y_train_4.replace(2, 0)
del y_train_4

## Обучение<a class="anchor" id="chapter5"></a>

1. проверка по часу
2. проверка по минуте
3. провкерка мультиклассовой классификации
4. Отделить данные с агуста 2020
5. Топ признаки
6. Навороты

In [282]:
def j_score(y_true, y_pred):
    f1 = f1_score(y_true, y_pred)
    return 1 / (2 / f1 - 1)

In [283]:
j_score = make_scorer(j_score, greater_is_better=True)

In [500]:
def gsearch(X, y,
            model = DecisionTreeClassifier(random_state=0), 
            param_grid = {'max_features': ['auto', 'sqrt', 'log2'],
                          'ccp_alpha': [0.1, .01, .001],
                          'max_depth' : range(2, 20, 1),
                          'criterion' :['gini', 'entropy']
                         },
            n_jobs=-1,
            scoring=j_score,
            verbose=True):
    
    grid_search = GridSearchCV(
        estimator=model,
        scoring=j_score,
        param_grid=param_grid,
        n_jobs=-1,
        cv= TimeSeriesSplit(n_splits=5),
        verbose=True
    )
    grid_search.fit(X, y)
    return grid_search

# Изменение данных для 1ого столбца

## Ресемплирование по разным отрезкам

In [673]:
def resampling_func(X, y, res_per, col_num):
    """
    Вывод временных зависимостей для отдельного параметра

    Аргументы:
        X(pd.DataFrame): Таблицы признаков.
        y(pd.DataFrame): Таблица таргетов.
        res_per(str): Отрезок ресамплинга.
        col_num(int): Номер исследуемого признака.
        
    Вывод:
        list: Список из периода для ресамплинга и лучшего значения метрики.
    """
    
    X_train_res = X.resample(res_per).mean().interpolate()
    y_train_res = y.resample(res_per).max()
    
    grid = gsearch(X_train_res, y_train_res[y_train_res.columns[col_num]])
    
    return [res_per, grid.best_score_]

In [313]:
results_res = pd.DataFrame({
    'Period' : [],
    'Score' : [],
})

### Ресамплинг по дням, часу и 5 минутам

In [411]:
%%time
for per in ['1D', '1H', '5Min']:
    results_res.loc[len(results_res.index)] = resampling_func(X_train_4, y_train_m3, per, 0)

Fitting 5 folds for each of 324 candidates, totalling 1620 fits
CPU times: total: 3.92 s
Wall time: 4.7 s


In [412]:
results_res

Period     Score
0     1D  0.283323
1     1H  0.225396
2   5Min  0.251666
3     1D  0.283323
4     1D  0.283323
5     1D  0.283323

Лучше всего оказался отрезок в 1 день

In [328]:
X_train_1D = X_train_4.resample('1D').mean().interpolate()
y_train_1D = y_train_m3.resample('1D').max()

## Другие способы

**С балансировкой**

In [413]:
pipe = imbPipeline([
    ('oversampling', SMOTE(random_state=0)),
    ('dec_tree', DecisionTreeClassifier(random_state=0))
])

In [414]:
param_grid = {'dec_tree__ccp_alpha': [0.1, .01, .001],
              'dec_tree__max_depth' : range(5, 15, 2),
              'dec_tree__criterion' :['gini', 'entropy']
             }

In [416]:
grid = gsearch(X_train_1D, y_train_1D[y_train_1D.columns[0]], pipe, param_grid)
grid.best_score_

Fitting 5 folds for each of 30 candidates, totalling 150 fits


0.1862035396385316

Результат сильно ухудшился

**Данные только за полтора года**

In [417]:
%%time
grid = gsearch(X_train_1D['2020-08-01  00:00:00':], 
               y_train_1D[y_train_1D.columns[0]]['2020-08-01  00:00:00':])

grid.best_score_

Fitting 5 folds for each of 324 candidates, totalling 1620 fits
CPU times: total: 1.14 s
Wall time: 1.96 s


0.031249999999999993

Модель стала полностью непригодной

**Без столбцов корреляции**

In [342]:
to_drop_4 = ['ЭКСГАУСТЕР 4. ТОК РОТОРА2',
 'ЭКСГАУСТЕР 4. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 2',
 'ЭКСГАУСТЕР 4. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 3',
 'ЭКСГАУСТЕР 4. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 4',
 'ЭКСГАУСТЕР 4. ТЕМПЕРАТУРА МАСЛА В МАСЛОБЛОКЕ',
 'ЭКСГАУСТЕР 4. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 4',
 'ЭКСГАУСТЕР 4. ВИБРАЦИЯ НА ОПОРЕ 3. ПРОДОЛЬНАЯ.',
 'ЭКСГАУСТЕР 4. ВИБРАЦИЯ НА ОПОРЕ 4. ПРОДОЛЬНАЯ.']

In [348]:
X_train_drop = X_train_4.copy()
X_train_drop = X_train_drop.drop(to_drop_4, axis=1)

In [353]:
results_res_drop = pd.DataFrame({
    'Period' : [],
    'Score' : [],
})

In [354]:
%%time
for per in ['1D', '1H', '5Min']:
    results_res_drop.loc[len(results_res_drop.index)] = resampling_func(X_train_drop, y_train_m3, per, 0)

Fitting 5 folds for each of 324 candidates, totalling 1620 fits
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
CPU times: total: 27.4 s
Wall time: 2min 54s


In [355]:
results_res_drop

Period     Score
0     1D  0.197053
1     1H  0.262879
2   5Min  0.267233

In [356]:
results_res 

Period     Score
0     1D  0.283323
1     1H  0.225396
2   5Min  0.251666
3     1D  0.283323

Примечательно, что результат улучшился для ресамплинга по часу и 5ти минутам, но обычный ежедневный ресамплинг все-таки лучше без удаления коррелирующих столбцов

## Rolling means

### Rolling mean

In [674]:
def win_tendency(X, y, win_range, win_col_num, col_num):
    """
    Поиск тенденции для разных окон

    Аргументы:
        X(pd.DataFrame): Исходный датафрейм.
        y(pd.DataFrames): Таблица таргетов.
        win_range(range): Диапазон сдвигов.
        win_col_num(int): Номер сдвигаемого столбца.
        col_num(int): Номер исследуемого признака.
        
    Вывод:
        fig: График метрик для соответствующих сдвигов.
    """
    X = X.copy()
    cl = X.columns   
    res_ser = pd.DataFrame({'Win' : [], 'Score' : []})
    
    for win in win_range:
        X_temp = X.copy()
        X_temp[f'{win_col_num}_mean'] = X_temp[cl[win_col_num]].rolling(min_periods=1, window=win).mean()
        X_temp[f'{win_col_num}_median'] = X_temp[cl[win_col_num]].rolling(min_periods=1, window=win).median()
        X_temp[f'{win_col_num}_max'] = X_temp[cl[win_col_num]].rolling(min_periods=1, window=win).max()
        X_temp[f'{win_col_num}_min'] = X_temp[cl[win_col_num]].rolling(min_periods=1, window=win).min()        
        
        grid = gsearch(X_temp, y[y.columns[col_num]])

        del X_temp
        
        res_ser.loc[len(res_ser.index)] = [win, grid.best_score_]     
        
    fig = go.Figure()
    fig.add_trace(go.Scatter(x=res_ser['Win'], y=res_ser['Score']))
    
    return fig

In [600]:
win_tendency(X_train_1D, y_train_1D, range(11, 28, 1), 0, 0)

Fitting 5 folds for each of 324 candidates, totalling 1620 fits
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
Fitting 5 folds for each of 324 candidat

In [675]:
def window_add(X_train, y, window_range, col_num):
    """
    Поэтапное добавление новых оконных столбцов при улучшении скоргнка.

    Аргументы:
        X(pd.DataFrame): Исходный датафрейм.
        y(pd.DataFrames): Таблица таргетов.
        window_range(range): Диапазон поиска окна.
        col_num(int): Номер исследуемого признака.
        
    Выводы:
        tuple: Кортеж из элементов:
            - pd.DataFrame: Улучшенный датасет.
            - pd.DataFrame: Таблица с данными о добавленных столбцах и соответствующих им окон.
    """

    X = X_train.copy()
    cl = X.columns
    base_score = gsearch(X, y[y.columns[col_num]], verbose=0).best_score_
    print(base_score)
    
    best_rolls = pd.DataFrame({'Column_number' : [], 'Name' : [], 'Window' : [], 'Best_rol' : []})
    
    # Пройдемся по всем колонкам изначального датафрейма
    for cind in range(len(cl) - 1):
        print(cind)
        res_ser = pd.DataFrame({'Window' : [], 'Score' : []}) # Временный столбец скорингов этого столбца для разных размеров окон
        
         # Создаем различные окна и проверяем их
        for i in window_range:
            X_temp = X.copy()

            X_temp[f'{cind}_mean'] = X_temp[cl[cind]].rolling(min_periods=1, window=i).mean()
            X_temp[f'{cind}_median'] = X_temp[cl[cind]].rolling(min_periods=1, window=i).median()
            X_temp[f'{cind}_max'] = X_temp[cl[cind]].rolling(min_periods=1, window=i).max()
            X_temp[f'{cind}_min'] = X_temp[cl[cind]].rolling(min_periods=1, window=i).min()

            grid = gsearch(X_temp, y[y.columns[col_num]], verbose=0)

            del X_temp
            print(i, grid.best_score_)

            res_ser.loc[len(res_ser.index)] = [i, grid.best_score_]  # Сохраняем результат данного окна в лучшей конфигурации модели        

        print(res_ser['Score'].max())
        if res_ser['Score'].max() > base_score: # Проверяем, улучшит ли такое окно результат
            base_score = res_ser['Score'].max()
            window = int(res_ser.loc[res_ser['Score'] == res_ser['Score'].max(), 'Window'].values[0])
            # Обновляем датасет с лучшим результатом, в следующей иерации будем учиывать новые столбцы
            X[f'{cind}_mean_'] = X[cl[cind]].rolling(min_periods=1, window=window).mean()
            X[f'{cind}_median_'] = X[cl[cind]].rolling(min_periods=1, window=window).median()
            X[f'{cind}_max_'] = X[cl[cind]].rolling(min_periods=1, window=window).max()
            X[f'{cind}_min_'] = X[cl[cind]].rolling(min_periods=1, window=window).min()

            best_rolls.loc[len(best_rolls.index)] = [
                cind, 
                f'{cl[cind]}', 
                window, 
                base_score
            ]
    return X, best_rolls

In [617]:
(X_train_1D_roll, best_rolls) = window_add(X_train_1D, y_train_1D, range(11, 28, 1), 0)

Fitting 5 folds for each of 324 candidates, totalling 1620 fits
0.2833225862854305
0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
11 0.18188567630442007
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
12 0.1776687683900799
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
13 0.18262812755350072
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
14 0.1980448717948718
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
15 0.20720462543991958
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
16 0.20621794871794874
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
17 0.23501501501501504
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
18 0.275952380952381
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
19 0.19322775263951736
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
20 0.20153153153153153
Fitting 5 folds for each of 324 candidates, total

18 0.29427816820541086
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
19 0.274310729920486
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
20 0.2828210678210678
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
21 0.29423809523809524
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
22 0.27978253603402087
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
23 0.2588007157583537
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
24 0.2633967401874976
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
25 0.23866933689363598
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
26 0.2157079343365253
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
27 0.2712820512820513
0.32959532749269915
6
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
11 0.3108365182907554
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
12 0.30436695307336414
Fittin

27 0.2427823514384369
0.35012820512820514
11
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
11 0.2722651222651223
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
12 0.27660894660894664
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
13 0.27879599151488554
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
14 0.28642129555944607
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
15 0.2952901341643881
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
16 0.29964592007401875
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
17 0.20769404943442024
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
18 0.21877359329221355
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
19 0.22563109354413702
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
20 0.2725345622119816
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
21 0.21617481971775368
F

In [620]:
cnum_w = best_rolls[['Column_number', 'Window']]
best_rolls

Column_number                                             Name  Window   
0              3           ЭКСГАУСТЕР 4. ДАВЛЕНИЕ МАСЛА В СИСТЕМЕ      20  \
1              4  ЭКСГАУСТЕР 4. ТЕМПЕРАТУРА ПОДШИПНИКА НА ОПОРЕ 1      23   
2              9     ЭКСГАУСТЕР 4. ТЕМПЕРАТУРА МАСЛА В МАСЛОБЛОКЕ      24   

   Best_rol  
0  0.321847  
1  0.358632  
2  0.418068

### Среднеквадратичное отклонение от окна

In [676]:
def window_add_std(X_train, y, cnum_w, col_num):
    """
    Добавление среднеквадратичного отклонения от оконных значений

    Аргументы:
        X(pd.DataFrame): Исходный датафрейм.
        y(pd.DataFrames): Таблица таргетов.
        cnum_w(pd.DataFrames): Таблица номеров колонок и соответствующих окон.
        col_num(int): Номер исследуемого признака.
        
    Выводы:
        tuple: Кортеж из элементов:
            - pd.DataFrame: Улучшенный датасет.
            - float: Метрика с новыми столбцами.
    """

    X = X_train.copy()
    cl = X.columns

    for i in range(len(cnum_w)):
        cnum = cnum_w.loc[i, 'Column_number']
        window = cnum_w.loc[i, 'Window']
        X[f'{cnum}_mean_std'] = (X[f'{cnum}_mean_'] - X[cl[cnum]]) ** 2 / window
        X[f'{cnum}_median_std'] = (X[f'{cnum}_median_'] - X[cl[cnum]]) ** 2 / window
        X[f'{cnum}_max_std'] = (X[f'{cnum}_max_'] - X[cl[cnum]]) ** 2 / window
        X[f'{cnum}_min_std'] = (X[f'{cnum}_min_'] - X[cl[cnum]]) ** 2 / window
        
    grid = gsearch(X, y[y.columns[col_num]], verbose=0)
    
    return X, grid.best_score_

In [491]:
(X_train_1D_roll_std, std_score) = window_add_std(X_train_1D_roll, y_train_1D, cnum_w, 0)
std_score

Fitting 5 folds for each of 324 candidates, totalling 1620 fits


0.25415288379983036

Результат значительно ухудшился

In [492]:
del X_train_1D_roll_std

### max - min

In [677]:
def window_add_std(X_train, y, cnum_w, col_num):
    """
    Добавление среднеквадратичного отклонения от оконных значений

    Аргументы:
        X(pd.DataFrame): Исходный датафрейм.
        y(pd.DataFrames): Таблица таргетов.
        cnum_w(pd.DataFrames): Таблица номеров колонок и соответствующих окон.
        col_num(int): Номер исследуемого признака.
        
    Выводы:
        tuple: Кортеж из элементов:
            - pd.DataFrame: Улучшенный датасет.
            - float: Метрика с новыми столбцами.
    """

    X = X_train.copy()
    cl = X.columns
    
    for i in range(len(cnum_w)):
        cnum = cnum_w.loc[i, 'Column_number']
        X[f'{cnum}_mm'] = X[f'{cnum}_max_'] - X[f'{cnum}_min_']
        
    grid = gsearch(X, y[y.columns[col_num]])
    
    return X, grid.best_score_

In [494]:
(X_train_1D_roll_mm, mm_score) = window_add_std(X_train_1D_roll, y_train_1D, cnum_w, 0)
mm_score

Fitting 5 folds for each of 324 candidates, totalling 1620 fits


0.3287657823376354

Значение снова ухудшилось

In [495]:
del X_train_1D_roll_mm

### Отклонение от среднего

In [678]:
def window_mean_diff(X_train, y, cnum_w, col_num):
    """
    Добавление отклонения от средних значений

    Аргументы:
        X(pd.DataFrame): Исходный датафрейм.
        y(pd.DataFrames): Таблица таргетов.
        cnum_w(pd.DataFrames): Таблица номеров колонок и соответствующих окон.
        col_num(int): Номер исследуемого признака.
        
    Выводы:
        tuple: Кортеж из элементов:
            - pd.DataFrame: Улучшенный датасет.
            - float: Метрика с новыми столбцами.
    """

    X = X_train.copy()
    cl = X.columns
    
    for i in range(len(cnum_w)):
        cnum = cnum_w.loc[i, 'Column_number']
        X[f'{cnum}_mm'] = X[f'{cnum}_mean_'] - X[cl[cnum]]
        
    grid = gsearch(X, y[y.columns[col_num]])
    
    return X, grid.best_score_

In [559]:
(X_train_1D_roll_md, md_score) = window_mean_diff(X_train_1D_roll, y_train_1D, cnum_w, 0)
md_score

Fitting 5 folds for each of 324 candidates, totalling 1620 fits


0.2892294372294372

In [560]:
del X_train_1D_roll_md

### Отношение к среднему

In [679]:
def window_mean_ratio(X_train, y, cnum_w, col_num):
    """
    Добавление среднеквадратичного отклонения от оконных значений

    Аргументы:
        X(pd.DataFrame): Исходный датафрейм.
        y(pd.DataFrames): Таблица таргетов.
        cnum_w(pd.DataFrames): Таблица номеров колонок и соответствующих окон.
        col_num(int): Номер исследуемого признака.
        
    Выводы:
        tuple: Кортеж из элементов:
            - pd.DataFrame: Улучшенный датасет.
            - float: Метрика с новыми столбцами.
    """

    X = X_train.copy()
    cl = X.columns

    for i in range(len(cnum_w)):
        cnum = cnum_w.loc[i, 'Column_number']
        X[f'{cnum}_mean_std'] =  X[cl[cnum]] / X[f'{cnum}_mean_']
        
    grid = gsearch(X, y[y.columns[col_num]], verbose=0)
    
    return X, grid.best_score_

In [563]:
(X_train_1D_roll_mr, mr_score) = window_mean_ratio(X_train_1D_roll, y_train_1D, cnum_w, 0)
std_score

Fitting 5 folds for each of 324 candidates, totalling 1620 fits


0.25415288379983036

In [564]:
del X_train_1D_roll_mr

## lag

Проверим тенденцию для одного столбца

In [680]:
def lag_tendency(X, y, lag_range, lag_col_num, col_num):
    """
    Поиск тенденции для разных сдвигов

    Аргументы:
        X(pd.DataFrame): Исходный датафрейм.
        y(pd.DataFrames): Таблица таргетов.
        lag_range(range): Диапазон сдвигов.
        lag_col_num(int): Номер сдвигаемого столбца.
        col_num(int): Номер исследуемого признака.
        
    Вывод:
        fig: График метрик для соответствующих сдвигов.
    """
    X = X.copy()
    cl = X.columns   
    res_ser = pd.DataFrame({'Lag' : [], 'Score' : []})
    
    for lag in lag_range:
        X_temp = X.copy()
        X_temp[f'{lag_col_num}_lag'] = X_temp[cl[lag_col_num]].shift(lag)
        X_temp = X_temp.fillna(0)

        grid = gsearch(X_temp, y[y.columns[col_num]])

        del X_temp
        
        res_ser.loc[len(res_ser.index)] = [lag, grid.best_score_]     
        
    fig = go.Figure()
    fig.add_trace(go.Scatter(x=res_ser['Lag'], y=res_ser['Score']))
    
    return fig

In [536]:
fig = lag_tendency(X_train_1D_roll, y_train_1D, range(0, 20, 1), 11, 0)

Fitting 5 folds for each of 324 candidates, totalling 1620 fits
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
Fitting 5 folds for each of 324 candidat

In [537]:
fig.show()

Судя по всему, выигрыш может дать только сдвиг на единицу

In [681]:
def lag_add(X_train, y, lag_range, col_num):
    """
    Поэтапное добавление сдвигов

    Аргументы:
        X_train(pd.DataFrame): Исходный датафрейм.
        y(pd.DataFrames): Таблица таргетов.
        lag_range(range): Диапазон сдвигов.
        col_num(int): Номер исследуемого признака.
        
    Вывод:
        fig: График метрик для соответствующих сдвигов.
    """
    X = X_train.copy()
    cl = X.columns
    base_score = gsearch(X, y[y.columns[col_num]], verbose=0).best_score_
    print(base_score)
    best_lag = pd.DataFrame({'Column_number' : [], 'Name' : [], 'lag' : [], 'best_score' : []})
    # Пройдемся по всем колонкам изначального датафрейма
    for cind in range(len(cl) - 1):
        res_ser = pd.DataFrame({'Lag' : [], 'Score' : []}) # Временный столбец скорингов этого столбца для разных размеров окон        
        for lag in lag_range:
            X_temp = X.copy()
            X_temp[f'{cind}_lag_{lag}'] = X_temp[cl[cind]].shift(lag)
            X_temp = X_temp.fillna(0)

            grid = gsearch(X_temp, y[y.columns[col_num]])
            print(grid.best_score_)

            del X_temp

            res_ser.loc[len(res_ser.index)] = [lag, grid.best_score_] 

        if res_ser['Score'].max() > base_score: # Проверяем, улучшит ли такое окно результат
            base_score = res_ser['Score'].max()
            lag = int(res_ser.loc[res_ser['Score'] == res_ser['Score'].max(), 'Lag'].values[0])
            # Обновляем датасет с лучшим результатом, в следующей иерации будем учиывать новые столбцы
            X[f'{cind}_lag_{lag}'] = X[cl[cind]].shift(lag)
            X = X.fillna(0)

            best_lag.loc[len(best_lag.index)] = [
                cind, 
                f'{cl[cind]}', 
                lag, 
                base_score
            ]            
            
    return X, best_lag

In [636]:
(X_train_1D_roll_lag, best_lag) = lag_add(X_train_1D_roll, y_train_1D, [1], 0)

Fitting 5 folds for each of 324 candidates, totalling 1620 fits
0.41806794777317985
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
0.4429009202179934
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
0.29002214839424145
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
0.3144123922966805
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
0.314058574792025
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
0.314058574792025
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
0.314058574792025
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
0.314058574792025
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
0.314058574792025
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
0.3268806992420564
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
0.314058574792025
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
0.314058574792025
Fitting 5

In [556]:
cnum_l = best_lag[['Column_number', 'lag']]
best_lag

Column_number                        Name  lag  best_score
0              0  ЭКСГАУСТЕР 4. ТОК РОТОРА 1    1    0.442901

### Разница с lag

In [592]:
def lag_add_diff(X_train, y, cnum_l, col_num):
    """
    Добавление среднеквадратичного отклонения от оконных значений

    Аргументы:
        X(pd.DataFrame): Исходный датафрейм.
        y(pd.DataFrames): Таблица таргетов.
        cnum_l(pd.DataFrames): Таблица номеров колонок и соответствующих сдвигов.
        col_num(int): Номер исследуемого признака.
        
    Выводы:
        tuple: Кортеж из элементов:
            - pd.DataFrame: Улучшенный датасет.
            - float: Метрика с новыми столбцами.
    """

    X = X_train.copy()
    cl = X.columns

    for i in range(len(cnum_l)):
        cnum = cnum_l.loc[i, 'Column_number']
        lag = cnum_l.loc[i, 'lag']
        X[f'{cnum}_lag_dif'] = X[cl[cnum]] - X[f'{cnum}_lag_{lag}']
        
    grid = gsearch(X, y[y.columns[col_num]], verbose=0)
    
    return X, grid.best_score_

In [554]:
(X_train_1D_roll_lag_diff, score) = lag_add_diff(X_train_1D_roll_lag, y_train_1D, cnum_l, 0)
score

Fitting 5 folds for each of 324 candidates, totalling 1620 fits


0.314058574792025

Отметаем

In [ ]:
del X_train_1D_roll_lag_diff

##  Предсказание

In [625]:
X_test_4 = dd_X_test_4.compute()

In [688]:
def i_transofm(X_test_4, res_per, best_rolls, best_lag):
    X_train_res = X_test_4.resample(res_per).mean().interpolate()
    
    cl = X_train_res.columns
    for i in range(len(best_rolls)):
        col = best_rolls['Column_number'][i]
        win = best_rolls['Window'][i]
        X_train_res[f'{col}_mean_'] = X_train_res[cl[col]].rolling(min_periods=1, window=win).mean()
        X_train_res[f'{col}_median_'] = X_train_res[cl[col]].rolling(min_periods=1, window=win).median()
        X_train_res[f'{col}_max_'] = X_train_res[cl[col]].rolling(min_periods=1, window=win).max()
        X_train_res[f'{col}_min_'] = X_train_res[cl[col]].rolling(min_periods=1, window=win).min()
        
    for i in range(len(best_lag)):
        col = best_lag['Column_number'][i]
        lag = best_lag['lag'][i]   
        X_train_res[f'{col}_lag_{lag}'] = X_train_res[cl[col]].shift(lag)
        X_train_res = X_train_res.fillna(0)
    
    return X_train_res

In [640]:
model = gsearch(X_train_1D_roll_lag, y_train_1D[y_train_1D.columns[0]], verbose=0).best_estimator_

Fitting 5 folds for each of 324 candidates, totalling 1620 fits


In [650]:
X_test_4_0 = i_transofm(X_test_4, '1D', best_rolls, best_lag)

In [658]:
y_0 = model.predict(X_test_4_0)
y_0_df = pd.DataFrame({y_train_1D.columns[0] : y_0}, index = X_test_4_0.index).replace(1, 2)
y_0_res = y_0_df.resample('10s').ffill()

In [668]:
del X_test_4_0

# То же самое для остальных колонок

In [572]:
del X_train_1D_roll_lag, X_train_1D_roll

In [766]:
def shortcut(y_col):
    Y_COL = y_col
    
    results_res_i = pd.DataFrame({
        'Period' : [],
        'Score' : [],
    })
    
    # Resamplimg
    
    for per in ['1D', '1H', '5Min']:
        results_res_i.loc[len(results_res_i.index)] = resampling_func(X_train_4, y_train_m3, per, Y_COL)
        
    res_per = results_res_i.sort_values(by='Score', ascending=False).loc[0, 'Period'] # best
    
    X_train_res = X_train_4.resample(res_per).mean().interpolate()
    y_train_res = y_train_m3.resample(res_per).max()
    
    #window
    
    (X_train_res_roll, best_rolls) = window_add(X_train_res, y_train_res, range(1, 83, 2), Y_COL)
    
    #lag
    
    (X_train_res_roll_lag, best_lag) = lag_add(X_train_res_roll, y_train_res, [1], Y_COL)
    
    grid = gsearch(X_train_res_roll_lag, y_train_res[y_train_res.columns[Y_COL]], verbose=0)
    model  = grid.best_estimator_
    score = grid.best_score_
    
    return model, score, res_per, best_rolls, best_lag

In [767]:
(model, score, res_per, best_rolls, best_lag) = shortcut(1)
score

Fitting 5 folds for each of 324 candidates, totalling 1620 fits
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
0.6242222222222222
0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
1 0.5988888888888889
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
3 0.6066666666666667
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
5 0.5722222222222222
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
7 0.6233333333333333
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
9 0.6233333333333333
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
11 0.6233333333333333
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
13 0.6166666666666667
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
15 0.6166666666666666
Fitting 5 folds for each of 324 candidat

21 0.616996996996997
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
23 0.616996996996997
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
25 0.616996996996997
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
27 0.616996996996997
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
29 0.616996996996997
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
31 0.616996996996997
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
33 0.616996996996997
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
35 0.616996996996997
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
37 0.674040404040404
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
39 0.674040404040404
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
41 0.674040404040404
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
43 0.674040404040404
Fitting 5 folds for each of 324 candidates, 

49 0.616996996996997
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
51 0.616996996996997
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
53 0.616996996996997
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
55 0.616996996996997
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
57 0.616996996996997
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
59 0.616996996996997
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
61 0.616996996996997
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
63 0.616996996996997
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
65 0.616996996996997
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
67 0.616996996996997
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
69 0.616996996996997
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
71 0.616996996996997
Fitting 5 folds for each of 324 candidates, 

79 0.616996996996997
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
81 0.616996996996997
0.616996996996997
7
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
1 0.616996996996997
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
3 0.616996996996997
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
5 0.616996996996997
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
7 0.616996996996997
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
9 0.616996996996997
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
11 0.616996996996997
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
13 0.616996996996997
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
15 0.616996996996997
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
17 0.616996996996997
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
19 0.616996996996997
Fitting 5 folds for each of 3

25 0.616996996996997
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
27 0.616996996996997
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
29 0.616996996996997
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
31 0.616996996996997
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
33 0.616996996996997
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
35 0.616996996996997
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
37 0.616996996996997
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
39 0.616996996996997
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
41 0.616996996996997
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
43 0.616996996996997
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
45 0.616996996996997
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
47 0.616996996996997
Fitting 5 folds for each of 324 candidates, 

55 0.616996996996997
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
57 0.616996996996997
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
59 0.616996996996997
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
61 0.616996996996997
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
63 0.616996996996997
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
65 0.616996996996997
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
67 0.616996996996997
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
69 0.616996996996997
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
71 0.616996996996997
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
73 0.616996996996997
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
75 0.616996996996997
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
77 0.616996996996997
Fitting 5 folds for each of 324 candidates, 

1 0.616996996996997
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
3 0.616996996996997
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
5 0.616996996996997
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
7 0.616996996996997
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
9 0.616996996996997
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
11 0.616996996996997
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
13 0.616996996996997
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
15 0.616996996996997
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
17 0.616996996996997
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
19 0.616996996996997
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
21 0.616996996996997
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
23 0.616996996996997
Fitting 5 folds for each of 324 candidates, total

0.711111111111111

In [768]:
score

0.711111111111111

In [769]:
X_test_4_1 = i_transofm(X_test_4, res_per, best_rolls, best_lag)

In [770]:
y_1 = model.predict(X_test_4_1)
y_1_df = pd.DataFrame({y_train_m3.columns[1] : y_1}, index = X_test_4_1.index).replace(1, 2)
y_1_res = y_1_df.resample('10s').ffill()

In [731]:
del X_test_4_1

In [685]:
(model, score, res_per, best_rolls, best_lag) = shortcut(2)
score

Fitting 5 folds for each of 324 candidates, totalling 1620 fits
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
0.9400000000000001
0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
1 0.9400000000000001
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
3 0.9400000000000001
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
5 0.9400000000000001
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
7 0.9400000000000001
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
9 0.9400000000000001
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
11 0.9400000000000001
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
13 0.9400000000000001
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
15 0.9400000000000001
Fitting 5 folds for each of 324 candidat

19 0.9400000000000001
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
21 0.9400000000000001
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
23 0.9400000000000001
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
25 0.9115325670498085
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
27 0.9076942838792551
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
29 0.9111695906432749
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
31 0.8853405017921148
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
33 0.8910966810966812
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
35 0.8949415204678364
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
37 0.8969021339220014
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
39 0.9129828486204324
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
41 0.9124024024024024
Fitting 5 folds for each of 324 

47 0.9400000000000001
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
49 0.9400000000000001
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
51 0.9400000000000001
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
53 0.9400000000000001
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
55 0.9400000000000001
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
57 0.9400000000000001
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
59 0.9400000000000001
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
61 0.9400000000000001
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
63 0.9400000000000001
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
65 0.9400000000000001
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
67 0.9400000000000001
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
69 0.9400000000000001
Fitting 5 folds for each of 324 

73 0.9400000000000001
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
75 0.9400000000000001
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
77 0.9400000000000001
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
79 0.9400000000000001
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
81 0.9400000000000001
0.9400000000000001
7
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
1 0.9400000000000001
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
3 0.9400000000000001
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
5 0.9400000000000001
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
7 0.9400000000000001
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
9 0.9400000000000001
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
11 0.9400000000000001
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
13 0.9400000000000001
Fitting 5 folds 

17 0.9400000000000001
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
19 0.9400000000000001
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
21 0.9400000000000001
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
23 0.9400000000000001
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
25 0.9400000000000001
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
27 0.9400000000000001
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
29 0.9400000000000001
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
31 0.9400000000000001
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
33 0.9400000000000001
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
35 0.9400000000000001
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
37 0.9400000000000001
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
39 0.9400000000000001
Fitting 5 folds for each of 324 

43 0.9400000000000001
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
45 0.9400000000000001
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
47 0.9400000000000001
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
49 0.9400000000000001
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
51 0.9400000000000001
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
53 0.9400000000000001
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
55 0.9400000000000001
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
57 0.9400000000000001
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
59 0.9400000000000001
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
61 0.9400000000000001
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
63 0.9400000000000001
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
65 0.9400000000000001
Fitting 5 folds for each of 324 

69 0.9400000000000001
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
71 0.9400000000000001
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
73 0.9400000000000001
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
75 0.9400000000000001
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
77 0.9400000000000001
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
79 0.9400000000000001
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
81 0.9400000000000001
0.9400000000000001
14
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
1 0.9400000000000001
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
3 0.9400000000000001
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
5 0.9400000000000001
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
7 0.9400000000000001
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
9 0.9400000000000001
Fitting 5 folds

0.945138888888889

In [686]:
score

0.945138888888889

In [689]:
X_test_4_2 = i_transofm(X_test_4, res_per, best_rolls, best_lag)

In [690]:
y_2 = model.predict(X_test_4_2)
y_2_df = pd.DataFrame({y_train_m3.columns[2] : y_2}, index = X_test_4_2.index).replace(1, 2)
y_2_res = y_2_df.resample('10s').ffill()

In [691]:
del X_test_4_2

In [692]:
(model, score, res_per, best_rolls, best_lag) = shortcut(3)
score

Fitting 5 folds for each of 324 candidates, totalling 1620 fits
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
0.6114689265536724
0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
1 0.6811111111111111
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
3 0.6877777777777777
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
5 0.6988888888888888
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
7 0.7022222222222222
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
9 0.688888888888889
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
11 0.7044444444444445
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
13 0.7100000000000001
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
15 0.7066666666666668
Fitting 5 folds for each of 324 candidate

21 0.7501433691756273
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
23 0.7501433691756273
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
25 0.7501433691756273
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
27 0.7501433691756273
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
29 0.7501433691756273
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
31 0.7501433691756273
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
33 0.7501433691756273
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
35 0.7501433691756273
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
37 0.7501433691756273
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
39 0.7501433691756273
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
41 0.7501433691756273
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
43 0.7501433691756273
Fitting 5 folds for each of 324 

47 0.7501433691756273
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
49 0.7501433691756273
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
51 0.7501433691756273
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
53 0.7501433691756273
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
55 0.7501433691756273
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
57 0.7501433691756273
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
59 0.7501433691756273
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
61 0.7501433691756273
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
63 0.7501433691756273
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
65 0.7501433691756273
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
67 0.7501433691756273
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
69 0.7501433691756273
Fitting 5 folds for each of 324 

73 0.7501433691756273
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
75 0.7501433691756273
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
77 0.7501433691756273
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
79 0.7501433691756273
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
81 0.7501433691756273
0.7501433691756273
7
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
1 0.7501433691756273
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
3 0.7501433691756273
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
5 0.7501433691756273
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
7 0.7501433691756273
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
9 0.7501433691756273
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
11 0.7501433691756273
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
13 0.7501433691756273
Fitting 5 folds 

17 0.7501433691756273
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
19 0.7501433691756273
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
21 0.7501433691756273
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
23 0.7501433691756273
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
25 0.7501433691756273
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
27 0.7501433691756273
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
29 0.7501433691756273
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
31 0.7501433691756273
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
33 0.7501433691756273
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
35 0.7501433691756273
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
37 0.7501433691756273
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
39 0.7501433691756273
Fitting 5 folds for each of 324 

43 0.7501433691756273
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
45 0.7501433691756273
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
47 0.7501433691756273
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
49 0.7501433691756273
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
51 0.7501433691756273
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
53 0.7501433691756273
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
55 0.7501433691756273
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
57 0.7501433691756273
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
59 0.7501433691756273
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
61 0.7501433691756273
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
63 0.7501433691756273
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
65 0.7501433691756273
Fitting 5 folds for each of 324 

69 0.7501433691756273
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
71 0.7501433691756273
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
73 0.7501433691756273
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
75 0.7501433691756273
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
77 0.7501433691756273
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
79 0.7501433691756273
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
81 0.7501433691756273
0.7501433691756273
14
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
1 0.7501433691756273
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
3 0.7501433691756273
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
5 0.7501433691756273
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
7 0.7501433691756273
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
9 0.7501433691756273
Fitting 5 folds

0.7566666666666667

In [693]:
score

0.7566666666666667

In [694]:
X_test_4_3 = i_transofm(X_test_4, res_per, best_rolls, best_lag)

In [695]:
y_3 = model.predict(X_test_4_3)
y_3_df = pd.DataFrame({y_train_m3.columns[3] : y_3}, index = X_test_4_3.index).replace(1, 2)
y_3_res = y_3_df.resample('10s').ffill()

In [696]:
del X_test_4_3

In [697]:
(model, score, res_per, best_rolls, best_lag) = shortcut(4)
score

Fitting 5 folds for each of 324 candidates, totalling 1620 fits
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
0.0
0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
1 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
3 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
5 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
7 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
9 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
11 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
13 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
15 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
17 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
19 0.0
Fitting 5 folds for each of 324 c

59 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
61 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
63 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
65 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
67 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
69 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
71 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
73 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
75 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
77 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
79 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
81 0.0
0.0
3
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
1 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
3 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
5 

45 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
47 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
49 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
51 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
53 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
55 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
57 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
59 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
61 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
63 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
65 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
67 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
69 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
71 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
73 0.0

31 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
33 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
35 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
37 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
39 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
41 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
43 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
45 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
47 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
49 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
51 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
53 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
55 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
57 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
59 0.0

17 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
19 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
21 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
23 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
25 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
27 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
29 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
31 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
33 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
35 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
37 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
39 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
41 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
43 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
45 0.0

3 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
5 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
7 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
9 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
11 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
13 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
15 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
17 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
19 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
21 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
23 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
25 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
27 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
29 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
31 0.0
Fit

0.0

In [698]:
score

0.0

In [699]:
X_test_4_4 = i_transofm(X_test_4, res_per, best_rolls, best_lag)

In [700]:
y_4 = model.predict(X_test_4_4)
y_4_df = pd.DataFrame({y_train_m3.columns[4] : y_4}, index = X_test_4_4.index).replace(1, 2)
y_4_res = y_4_df.resample('10s').ffill()

In [701]:
del X_test_4_4

In [702]:
(model, score, res_per, best_rolls, best_lag) = shortcut(5)
score

Fitting 5 folds for each of 324 candidates, totalling 1620 fits
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
0.0
0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
1 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
3 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
5 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
7 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
9 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
11 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
13 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
15 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
17 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
19 0.0
Fitting 5 folds for each of 324 c

59 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
61 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
63 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
65 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
67 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
69 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
71 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
73 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
75 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
77 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
79 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
81 0.0
0.0
3
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
1 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
3 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
5 

45 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
47 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
49 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
51 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
53 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
55 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
57 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
59 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
61 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
63 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
65 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
67 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
69 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
71 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
73 0.0

31 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
33 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
35 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
37 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
39 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
41 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
43 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
45 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
47 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
49 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
51 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
53 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
55 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
57 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
59 0.0

17 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
19 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
21 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
23 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
25 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
27 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
29 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
31 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
33 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
35 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
37 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
39 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
41 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
43 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
45 0.0

3 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
5 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
7 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
9 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
11 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
13 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
15 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
17 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
19 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
21 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
23 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
25 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
27 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
29 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
31 0.0
Fit

0.0

In [703]:
score

0.0

In [704]:
X_test_4_5 = i_transofm(X_test_4, res_per, best_rolls, best_lag)

In [705]:
y_5 = model.predict(X_test_4_5)
y_5_df = pd.DataFrame({y_train_m3.columns[5] : y_5}, index = X_test_4_5.index).replace(1, 2)
y_5_res = y_5_df.resample('10s').ffill()

In [706]:
del X_test_4_5

In [707]:
(model, score, res_per, best_rolls, best_lag) = shortcut(6)
score

Fitting 5 folds for each of 324 candidates, totalling 1620 fits
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
0.0
0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
1 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
3 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
5 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
7 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
9 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
11 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
13 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
15 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
17 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
19 0.0
Fitting 5 folds for each of 324 c

59 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
61 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
63 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
65 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
67 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
69 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
71 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
73 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
75 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
77 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
79 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
81 0.0
0.0
3
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
1 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
3 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
5 

45 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
47 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
49 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
51 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
53 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
55 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
57 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
59 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
61 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
63 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
65 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
67 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
69 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
71 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
73 0.0

31 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
33 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
35 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
37 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
39 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
41 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
43 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
45 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
47 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
49 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
51 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
53 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
55 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
57 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
59 0.0

17 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
19 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
21 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
23 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
25 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
27 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
29 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
31 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
33 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
35 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
37 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
39 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
41 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
43 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
45 0.0

3 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
5 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
7 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
9 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
11 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
13 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
15 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
17 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
19 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
21 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
23 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
25 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
27 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
29 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
31 0.0
Fit

0.0

In [708]:
score

0.0

In [709]:
X_test_4_6 = i_transofm(X_test_4, res_per, best_rolls, best_lag)

In [710]:
y_6 = model.predict(X_test_4_6)
y_6_df = pd.DataFrame({y_train_m3.columns[6] : y_6}, index = X_test_4_6.index).replace(1, 2)
y_6_res = y_6_df.resample('10s').ffill()

In [711]:
del X_test_4_6

In [712]:
(model, score, res_per, best_rolls, best_lag) = shortcut(7)
score

Fitting 5 folds for each of 324 candidates, totalling 1620 fits
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
0.2055060408001584
0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
1 0.24577990066282468
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
3 0.19473037939532784
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
5 0.18299859547590946
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
7 0.16464581411046364
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
9 0.24713489409141584
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
11 0.14733005733005736
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
13 0.22494286174150974
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
15 0.12888888888888891
Fitting 5 folds for each of 324 

19 0.21629582085294538
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
21 0.22119918699186997
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
23 0.2547803725326661
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
25 0.2515552643075579
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
27 0.2529486446995331
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
29 0.2541478569001504
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
31 0.25083214793741104
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
33 0.22616306557794003
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
35 0.2311926605504587
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
37 0.2654937150589325
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
39 0.2667261904761904
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
41 0.26380952380952377
Fitting 5 folds for each of

45 0.36984026579771256
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
47 0.23098901098901098
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
49 0.33727567691733423
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
51 0.33979736575481256
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
53 0.36831995427740105
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
55 0.34546281142025814
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
57 0.3518120177694645
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
59 0.36654456654456646
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
61 0.3681578468812511
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
63 0.3681578468812511
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
65 0.33979736575481256
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
67 0.35184925250669574
Fitting 5 folds for eac

71 0.3357867880651822
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
73 0.3518120177694645
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
75 0.3495563786717202
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
77 0.34992267903802055
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
79 0.34824058919803597
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
81 0.34633416229160907
0.35657392253136927
7
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
1 0.3303834463408931
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
3 0.3303834463408931
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
5 0.3303834463408931
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
7 0.3303834463408931
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
9 0.3403800691034734
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
11 0.31567950929653055
Fitting 5 f

15 0.31969331817607677
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
17 0.3541257441454711
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
19 0.3505395372489194
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
21 0.35730876801815015
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
23 0.34477938435833166
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
25 0.34477938435833166
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
27 0.34477938435833166
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
29 0.34057594858484735
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
31 0.35065297138664714
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
33 0.33536148062463855
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
35 0.3490419771799082
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
37 0.3196211564547397
Fitting 5 folds for each

41 0.2817933560692182
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
43 0.30155205797910767
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
45 0.3092834570148545
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
47 0.27006593406593415
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
49 0.27473260073260075
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
51 0.29139926739926747
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
53 0.28747014318498243
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
55 0.27406593406593405
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
57 0.27406593406593405
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
59 0.2947555892383479
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
61 0.2947555892383479
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
63 0.29367032967032963
Fitting 5 folds for each

67 0.3051958537915985
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
69 0.31274279343844563
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
71 0.3243369963369963
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
73 0.3383720840562946
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
75 0.3383720840562946
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
77 0.3173194524773473
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
79 0.31291637582018705
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
81 0.31885388182574187
0.3844194047837509
14
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
1 0.3321611721611722
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
3 0.3170367563471011
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
5 0.3142958191234053
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
7 0.32994828700711054
Fitting 5 

0.3933421985815603

In [713]:
score

0.3933421985815603

In [714]:
X_test_4_7 = i_transofm(X_test_4, res_per, best_rolls, best_lag)

In [715]:
y_7 = model.predict(X_test_4_7)
y_7_df = pd.DataFrame({y_train_m3.columns[7] : y_7}, index = X_test_4_7.index).replace(1, 2)
y_7_res = y_7_df.resample('10s').ffill()

In [716]:
del X_test_4_7

In [771]:
(model, score, res_per, best_rolls, best_lag) = shortcut(8)
score

Fitting 5 folds for each of 324 candidates, totalling 1620 fits
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
0.2797595112678156
0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
1 0.2725722046367244
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
3 0.273804502130601
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
5 0.3379996075199183
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
7 0.3130662864056693
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
9 0.2562600662022627
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
11 0.33243226357975897
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
13 0.23367031184281678
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
15 0.2760915386931647
Fitting 5 folds for each of 324 candida

19 0.26281746031746034
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
21 0.26281746031746034
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
23 0.26281746031746034
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
25 0.26281746031746034
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
27 0.26281746031746034
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
29 0.26281746031746034
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
31 0.26281746031746034
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
33 0.26281746031746034
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
35 0.26281746031746034
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
37 0.26281746031746034
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
39 0.26281746031746034
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
41 0.26281746031746034
Fitting 5 folds for 

43 0.26281746031746034
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
45 0.26281746031746034
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
47 0.26281746031746034
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
49 0.26281746031746034
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
51 0.26281746031746034
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
53 0.26281746031746034
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
55 0.26281746031746034
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
57 0.26281746031746034
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
59 0.26281746031746034
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
61 0.26281746031746034
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
63 0.26281746031746034
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
65 0.26281746031746034
Fitting 5 folds for 

67 0.26281746031746034
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
69 0.26281746031746034
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
71 0.26281746031746034
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
73 0.26281746031746034
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
75 0.26281746031746034
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
77 0.26281746031746034
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
79 0.26281746031746034
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
81 0.26281746031746034
0.26281746031746034
7
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
1 0.26281746031746034
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
3 0.26281746031746034
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
5 0.26281746031746034
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
7 0.26281746031746034
Fi

9 0.26281746031746034
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
11 0.26281746031746034
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
13 0.26281746031746034
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
15 0.26281746031746034
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
17 0.26281746031746034
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
19 0.26281746031746034
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
21 0.26281746031746034
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
23 0.26281746031746034
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
25 0.26281746031746034
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
27 0.26281746031746034
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
29 0.26281746031746034
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
31 0.26281746031746034
Fitting 5 folds for e

33 0.26281746031746034
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
35 0.26281746031746034
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
37 0.26281746031746034
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
39 0.26281746031746034
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
41 0.26281746031746034
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
43 0.26281746031746034
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
45 0.26281746031746034
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
47 0.26281746031746034
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
49 0.26281746031746034
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
51 0.26281746031746034
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
53 0.26281746031746034
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
55 0.26281746031746034
Fitting 5 folds for 

57 0.26281746031746034
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
59 0.26281746031746034
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
61 0.26281746031746034
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
63 0.26281746031746034
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
65 0.26281746031746034
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
67 0.26281746031746034
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
69 0.26281746031746034
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
71 0.26281746031746034
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
73 0.26281746031746034
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
75 0.26281746031746034
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
77 0.26281746031746034
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
79 0.26281746031746034
Fitting 5 folds for 

0.39711440723145636

In [772]:
score

0.39711440723145636

In [773]:
X_test_4_8 = i_transofm(X_test_4, res_per, best_rolls, best_lag)

In [774]:
y_8 = model.predict(X_test_4_8)
y_8_df = pd.DataFrame({y_train_m3.columns[8] : y_8}, index = X_test_4_8.index).replace(1, 2)
y_8_res = y_8_df.resample('10s').ffill()

In [775]:
del X_test_4_8

In [722]:
(model, score, res_per, best_rolls, best_lag) = shortcut(9)
score

Fitting 5 folds for each of 324 candidates, totalling 1620 fits
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
0.0
0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
1 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
3 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
5 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
7 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
9 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
11 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
13 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
15 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
17 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
19 0.0
Fitting 5 folds for each of 324 c

59 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
61 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
63 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
65 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
67 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
69 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
71 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
73 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
75 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
77 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
79 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
81 0.0
0.0
3
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
1 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
3 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
5 

45 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
47 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
49 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
51 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
53 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
55 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
57 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
59 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
61 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
63 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
65 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
67 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
69 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
71 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
73 0.0

31 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
33 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
35 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
37 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
39 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
41 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
43 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
45 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
47 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
49 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
51 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
53 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
55 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
57 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
59 0.0

17 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
19 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
21 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
23 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
25 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
27 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
29 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
31 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
33 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
35 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
37 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
39 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
41 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
43 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
45 0.0

3 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
5 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
7 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
9 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
11 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
13 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
15 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
17 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
19 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
21 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
23 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
25 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
27 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
29 0.0
Fitting 5 folds for each of 324 candidates, totalling 1620 fits
31 0.0
Fit

0.0

In [723]:
score

0.0

In [724]:
X_test_4_9 = i_transofm(X_test_4, res_per, best_rolls, best_lag)

In [725]:
y_9 = model.predict(X_test_4_9)
y_9_df = pd.DataFrame({y_train_m3.columns[9] : y_9}, index = X_test_4_9.index).replace(1, 2)
y_9_res = y_9_df.resample('10s').ffill()

In [726]:
del X_test_4_9

In [ ]:
(model, score, res_per, best_rolls, best_lag) = shortcut(10)
score

In [ ]:
X_test_4_10 = i_transofm(X_test_4, res_per, best_rolls, best_lag)

In [ ]:
y_10 = model.predict(X_test_4_10)
y_10_df = pd.DataFrame({y_train_m3.columns[10] : y_10}, index = X_test_4_10.index).replace(1, 2)
y_10_res = y_10_df.resample('10s').ffill()
del X_test_4_10

In [ ]:
(model, score, res_per, best_rolls, best_lag) = shortcut(11)
score


In [ ]:
X_test_4_11 = i_transofm(X_test_4, res_per, best_rolls, best_lag)

In [ ]:
y_11 = model.predict(X_test_4_11)
y_11_df = pd.DataFrame({y_train_m3.columns[11] : y_11}, index = X_test_4_11.index).replace(1, 2)
y_11_res = y_11_df.resample('10s').ffill()
del X_test_4_11


In [ ]:
(model, score, res_per, best_rolls, best_lag) = shortcut(12)
score

In [ ]:
X_test_4_12 = i_transofm(X_test_4, res_per, best_rolls, best_lag)

In [ ]:
y_12 = model.predict(X_test_4_12)
y_12_df = pd.DataFrame({y_train_m3.columns[12] : y_12}, index = X_test_4_12.index).replace(1, 2)
y_12_res = y_12_df.resample('10s').ffill()
del X_test_4_12

In [ ]:
(model, score, res_per, best_rolls, best_lag) = shortcut(13)
score


In [ ]:
X_test_4_13 = i_transofm(X_test_4, res_per, best_rolls, best_lag)

In [ ]:
y_13 = model.predict(X_test_4_13)
y_13_df = pd.DataFrame({y_train_m3.columns[13] : y_13}, index = X_test_4_13.index).replace(1, 2)
y_13_res = y_13_df.resample('10s').ffill()
del X_test_4_13


In [ ]:
(model, score, res_per, best_rolls, best_lag) = shortcut(14)
score


In [ ]:
X_test_4_14 = i_transofm(X_test_4, res_per, best_rolls, best_lag)

In [ ]:
y_14 = model.predict(X_test_4_14)
y_14_df = pd.DataFrame({y_train_m3.columns[14] : y_14}, index = X_test_4_14.index).replace(1, 2)
y_14_res = y_14_df.resample('10s').ffill()
del X_test_4_14


In [ ]:
(model, score, res_per, best_rolls, best_lag) = shortcut(15)
score


In [ ]:
X_test_4_15 = i_transofm(X_test_4, res_per, best_rolls, best_lag)

In [ ]:
y_15 = model.predict(X_test_4_15)
y_15_df = pd.DataFrame({y_train_m3.columns[15] : y_15}, index = X_test_4_15.index).replace(1, 2)
y_15_res = y_15_df.resample('10s').ffill()
del X_test_4_15


In [ ]:
(model, score, res_per, best_rolls, best_lag) = shortcut(16)
score


In [ ]:
X_test_4_16 = i_transofm(X_test_4, res_per, best_rolls, best_lag)

In [ ]:
y_16 = model.predict(X_test_4_16)
y_16_df = pd.DataFrame({y_train_m3.columns[16] : y_16}, index = X_test_4_16.index).replace(1, 2)
y_16_res = y_16_df.resample('10s').ffill()
del X_test_4_16


In [ ]:
(model, score, res_per, best_rolls, best_lag) = shortcut(17)
score


In [ ]:
X_test_4_17 = i_transofm(X_test_4, res_per, best_rolls, best_lag)

In [ ]:
y_17 = model.predict(X_test_4_17)
y_17_df = pd.DataFrame({y_train_m3.columns[17] : y_17}, index = X_test_4_17.index).replace(1, 2)
y_17_res = y_17_df.resample('10s').ffill()
del X_test_4_17


In [ ]:
(model, score, res_per, best_rolls, best_lag) = shortcut(18)
score


In [ ]:
X_test_4_18 = i_transofm(X_test_4, res_per, best_rolls, best_lag)

In [ ]:
y_18 = model.predict(X_test_4_18)
y_18_df = pd.DataFrame({y_train_m3.columns[18] : y_18}, index = X_test_4_18.index).replace(1, 2)
y_18_res = y_18_df.resample('10s').ffill()
del X_test_4_18


In [ ]:
(model, score, res_per, best_rolls, best_lag) = shortcut(19)
score


In [ ]:
X_test_4_19 = i_transofm(X_test_4, res_per, best_rolls, best_lag)

In [ ]:
y_19 = model.predict(X_test_4_19)
y_19_df = pd.DataFrame({y_train_m3.columns[19] : y_19}, index = X_test_4_19.index).replace(1, 2)
y_19_res = y_19_df.resample('10s').ffill()
del X_test_4_19


In [ ]:
(model, score, res_per, best_rolls, best_lag) = shortcut(20)
score


In [ ]:
X_test_4_20 = i_transofm(X_test_4, res_per, best_rolls, best_lag)

In [ ]:
y_20 = model.predict(X_test_4_20)
y_20_df = pd.DataFrame({y_train_m3.columns[20] : y_20}, index = X_test_4_20.index).replace(1, 2)
y_20_res = y_20_df.resample('10s').ffill()
del X_test_4_20


In [ ]:
(model, score, res_per, best_rolls, best_lag) = shortcut(21)
score


In [ ]:
X_test_4_21 = i_transofm(X_test_4, res_per, best_rolls, best_lag)

In [ ]:
y_21 = model.predict(X_test_4_21)
y_21_df = pd.DataFrame({y_train_m3.columns[21] : y_21}, index = X_test_4_21.index).replace(1, 2)
y_21_res = y_21_df.resample('10s').ffill()
del X_test_4_21


In [ ]:
(model, score, res_per, best_rolls, best_lag) = shortcut(22)
score


In [ ]:
X_test_4_22 = i_transofm(X_test_4, res_per, best_rolls, best_lag)

In [ ]:
y_22 = model.predict(X_test_4_22)
y_22_df = pd.DataFrame({y_train_m3.columns[22] : y_22}, index = X_test_4_22.index).replace(1, 2)
y_22_res = y_22_df.resample('10s').ffill()
del X_test_4_22


## Слияние

In [ ]:
y_test = y_0_res.join([y_1_res, y_2_res, y_3_res, 
                       y_4_res, y_5_res, y_6_res, 
                       y_7_res, y_8_res, y_9_res, 
                       y_9_res, y_9_res, y_9_res,
                       y_10_res, y_11_res, y_12_res,
                       y_13_res, y_14_res, y_15_res,
                       y_16_res, y_17_res, y_18_res,
                       y_19_res, y_20_res, y_21_res,
                       y_22_res])

In [ ]:
y_test = y_test.drop('DT', axis=1)
y_test = y_test.set_index(X_test_4.index)

y_test.to_csv(r'C:\Users\Мария\&hackaton\y_test.csv')